# Testing Tracery

From a GitHub gist [here](https://gist.github.com/aparrish/73c19a36b9cdcf604d04e95020418cd4)


Note: a great how-to guide [here](https://github.com/BenziAhamed/Tracery)

# Resources

- [Plaintext lists](https://www.plaintextlist.com) - not sure what usage but seems useable
- [Wordnet](https://wordnet.princeton.edu) - for dictionary, thesaurus
- [Squinky](https://www.groundai.com/project/squinky-a-corpus-of-sentence-level-formality-informativeness-and-implicature/2) - corpus of sentence-level formality. What is this? Will look later.

In [4]:
!pip3 install tracery

In [5]:
import tracery
from tracery.modifiers import base_english

rules = {
    "origin": "#hello.capitalize#, #location#!",
    "hello": ["hello", "greetings", "howdy", "hey"],
    "location": ["world", "solar system", "galaxy", "universe"]
}

grammar = tracery.Grammar(rules) # create a grammar object from the rules
grammar.add_modifiers(base_english) # add pre-programmed modifiers

for i in range(30):
    print (grammar.flatten("#origin#")) # and flatten, starting with origin rule


Greetings, world!
Hey, world!
Hello, universe!
Hey, solar system!
Hey, universe!
Hey, galaxy!
Howdy, solar system!
Howdy, galaxy!
Hey, universe!
Hey, solar system!
Hey, world!
Howdy, galaxy!
Howdy, universe!
Hey, galaxy!
Howdy, galaxy!
Hey, universe!
Greetings, universe!
Howdy, solar system!
Hey, solar system!
Howdy, solar system!
Greetings, world!
Howdy, universe!
Hello, galaxy!
Hey, solar system!
Howdy, solar system!
Hello, universe!
Greetings, universe!
Hello, world!
Hello, world!
Howdy, world!


What do I want from the generator?

The main thing works as follows:


- Define 2-5 local towns (e.g. Alphatown, Betatown, Charlietown, Deltatown) with one as main town (this becomes front page of directory)

- Generate types of business (in alphabetical order?)
    - Is this subject-level generation? e.g. aardvark, aardvark clearning, aardvark services, aardvark, etc? Or Aardvark, Betamax, etc?
    - How do we relate the genre of business to the businesses generated? Does the type of business become a tracery grammar?  
- Generate individual businesses.
    - Layout type. Options: 
        - Long / short
        - if long then number 0-10 (this becomes layout no, as in one two three - which then determines layout number loaded in static site generator).
        - if short then determine number between 1-100 to make X number of short entries; If short, then only generate name/address/phone no
    - e.g. within Aardvarks, Mick's Aardvark Company, Aardvark Incorporated, _thesaurus word for aardvark_ Services Inc, etc
    - Plus address:
        - Number (0-9999)
        - Street, Street type
        - Town - if in NOT MAIN town then perhaps the slogan becomes more competitive (e.g. "Don't pay TOWN A prices for your Aardvarks!", "Why go to the big city when you want Aardvarks? THE TOWN has all you need.", etc etc.
        - Zip code (define starting two digits for area, if TOWN A then next two digits defined? - how do US Zip codes work?)
    - Plus slogan:
        - FIRST WORD (e.g. Mick) has (it!) / (you (covered/sorted/etc)) / ((what/all/everything) you need / etc.) OR (BUSINESS_TYPE large and small / 
        - or random_adjective pl.BUSINESS_TYPE! random_adjective pl.BUSINESS_TYPE! random_adjective pl.BUSINESS_TYPE! (e.g. Red Aardvarks! Large Aardvarks! Triangular Aardvarks!)
        - Phone no. - AREA_CODE (determined by town), -###-####
    - Plus random number, 0-10000.png * 2 (one for bgd, one for foreground)
    
    - For each part of the info, check against database.db for that category - if it's already an entry, regenerate. If entire data is generated, save into DB.
    
    
    
These are saved as a MarkDown file:

- title (BUSINESS_NAME)
- layout (small / one/two/three/four/five)
- category (e.g. aardvarks)

and as an entry in the database.



Example of a small entries in the ELECTRICIAN category:

**F MASON & SONS LTD** 132 Heath St, Edgemonton. ☎ 434-7737  
**GERRY HEART ELECTRICIAN*** 552 Oakdale Ave, Beaverton. ☎ 434-9310


Which would be rendered in MarkDown as a file named f_mason_sons.md

```
---
layout: small
category: electrician
name: F. Mason & Sons Ltd
address: 132 Heath St, Edgemonton
phone: 434-7737
---
```

-----

So, let's go through those things in order:

# Town names

Let's just start with a phonetic alphabet, then generic town names like -ton, -chester, etc. These are loaded into the files ```corpora/townprefixes.txt``` and ```corpora/townsuffixes.txt```

In [159]:
with open('corpora/townprefixes.txt','r') as f:
    townprefixes = [line.strip() for line in f]
with open('corpora/townsuffixes.txt','r') as f:
    townsuffixes = [line.strip() for line in f]

print("prefixes = ",townprefixes)
print("suffixes =",townsuffixes)

# Let's test this

rules = {
    "origin": "#prefix.capitalize##suffix#",
    "prefix": townprefixes,
    "suffix": townsuffixes
}

grammar = tracery.Grammar(rules) # create a grammar object from the rules
grammar.add_modifiers(base_english) # add pre-programmed modifiers

for i in range(30):
    print (grammar.flatten("#origin#")) # and flatten, starting with origin rule

prefixes =  ['Alfa', 'Bravo', 'Charlie', 'Delta', 'Echo', 'Foxtrot', 'Golf', 'Hotel', 'India', 'Juliett', 'Kilo', 'Lima', 'Mike', 'November', 'Oscar', 'Papa', 'Quebec', 'Romeo', 'Sierra', 'Tango', 'Uniform', 'Victor', 'Whiskey', 'Xray', 'Yankee', 'Zulu']
suffixes = ['ville', 'town', 'ton', 'dam', 'ster', 'stone', 'ston', 'field', 'view', 'son', 'land', 'ford', 'bridge', 'port', 'burn', 'chester', 'side']
Novemberview
Bravoview
Limastone
Uniformside
Charliebridge
Victorland
Quebecfield
Sierraton
Papaston
Papaford
Deltafield
Kiloburn
Kiloson
Quebecside
Papaston
Kilofield
Uniformford
Alfaford
Mikeview
Romeoburn
Tangodam
Deltaside
Indiatown
Novemberport
Tangodam
Foxtrottown
Deltatown
Oscarport
Victorford
Victorburn


In [332]:
# Addresses

def loadData():
    with open('corpora/townprefixes.txt','r') as f:
        townprefixes = [line.strip() for line in f]
    with open('corpora/townsuffixes.txt','r') as f:
        townsuffixes = [line.strip() for line in f]
    with open('corpora/monopolystreets.txt','r') as f:
        street = [line.strip() for line in f]
    with open('corpora/words_alpha.txt','r') as f:
        words = [line.strip() for line in f]

    # print("prefixes = ",townprefixes)
    # print("suffixes =",townsuffixes)

loadData()

rules = {
    "address": "#number# #street.capitalize#, #town.capitalize#, #zipcode#",
    "number": ["#d0#","#d0##d#","#d0##d##d#","#d0##d##d#","#d0##d##d#","#d0##d##d#","#d0##d##d##d#","#d0##d##d##d#","#d0##d##d##d#","#d0##d##d##d#","#d0##d##d##d#","#d0##d##d##d#","#d0##d##d##d#","#d0##d##d##d#","#d0##d##d##d#"],
    "street": street,
    "town": "#prefix.capitalize##suffix#",
    "prefix": townprefixes,
    "suffix": townsuffixes,
    "zipcode": "#d##d##d##d##d#",
    "d":["0","1","2","3","4","5","6","7","8","9"],
    "d0":["1","2","3","4","5","6","7","8","9"],
    "words": words
}

grammar = tracery.Grammar(rules) # create a grammar object from the rules
grammar.add_modifiers(base_english) # add pre-programmed modifiers

for i in range(30):
    print (grammar.flatten("#address#")) # and flatten, starting with origin rule

445 Immobile, Papastone, 29113
6399 Asterioid, Echoford, 43954
995 Talas, Novemberburn, 10967
9224 Songlessly, Zuluton, 85530
758 Erythrean, Sierratown, 32263
6715 Dickite, Echoton, 33261
8552 Zendos, Sierrafield, 54945
954 Poisure, Uniformson, 29612
1062 Impanated, Foxtrotfield, 05070
88 Gapeseed, Charlieton, 23550
9804 Arciform, Papason, 14142
2908 Plumules, Victortown, 53931
9761 Subtend, Juliettburn, 61548
2318 Uninfluentiality, Bravoport, 12638
895 Grilladed, Limabridge, 47030
4841 Cariogenic, Zulutown, 32414
8906 Bacteriophagia, Juliettview, 18606
9806 Senders, Romeobridge, 36311
281 Bestraw, Bravoside, 42923
835 Ichneumones, Mikeport, 75433
5207 Jungliest, Zulutown, 47560
7677 Intrathoracic, Xrayston, 07320
58 Jaggery, Victorton, 26936
9233 Scotophilia, Charlieson, 76672
7832 Arginine, Papason, 09356
1479 Lensmen, Uniformton, 03234
2485 Flossie, Whiskeyville, 45311
1923 Alphonso, Xrayston, 88310
4162 Delicat, Alfadam, 98253
968 Admits, Foxtrotston, 87603


# zipcodes

Note that US zipcodes are v specific:

    - first digit is state (several states share each number)
    - second + third digits = sectional sorting code
    - fourth + fifth are specific towns, streets, etc
    
...but there are unused numbers! [See here](https://en.wikipedia.org/wiki/Sectional_center_facility)

So later on in the project, let's find ones that don't exist and use only those. That will probably locate us within a state or two too.


In [58]:
# NOTE THIS CELL DOESN'T WORK! LEFT IN JUST TO AVOID DOING IT AGAIN...WILL CLEAN UP AT END?

# let's try some variables, as taken from an example here > https://github.com/galaxykate/tracery/issues/14

rules = {
    "name": ["Cheri","Fox","Morgana","Jedoo","Brick","Shadow","Krox","Urga","Zelph"],
"story": ["#name.capitalize# was a great #occupation#, and this song tells of #heroTheir# adventure. #name.capitalize# #didStuff#, then #heroThey# #didStuff#, then #heroThey# went home to read a book."] ,
"monster": ["dragon","ogre","witch","wizard","goblin","golem","giant","sphinx","warlord"] , 
"setPronouns": ["[heroThey:they][heroThem:them][heroTheir:their][heroTheirs:theirs]","[heroThey:she][heroThem:her][heroTheir:her][heroTheirs:hers]","[heroThey:he][heroThem:him][heroTheir:his][heroTheirs:his]"] , "setOccupation": ["[occupation:baker][didStuff:baked bread,decorated cupcakes,folded dough,made croissants,iced a cake]","[occupation:warrior][didStuff:fought #monster.a#,saved a village from #monster.a#,battled #monster.a#,defeated #monster.a#]"] ,
"origin": ["#[#setPronouns#][#setOccupation#][hero:#name#]story#"]
}
grammar = tracery.Grammar(rules) # create a grammar object from the rules
grammar.add_modifiers(base_english) # add pre-programmed modifiers

for i in range(3):
    print (grammar.flatten("#story#")) # and flatten, starting with origin rule

Fox was a great ((occupation)), and this song tells of ((heroTheir)) adventure. Jedoo ((didStuff)), then ((heroThey)) ((didStuff)), then ((heroThey)) went home to read a book.
Zelph was a great ((occupation)), and this song tells of ((heroTheir)) adventure. Cheri ((didStuff)), then ((heroThey)) ((didStuff)), then ((heroThey)) went home to read a book.
Morgana was a great ((occupation)), and this song tells of ((heroTheir)) adventure. Jedoo ((didStuff)), then ((heroThey)) ((didStuff)), then ((heroThey)) went home to read a book.


In [80]:
class person(id):
    id = id
    print("poo")

symbols = {
    "like": ["benches", "trees", "grass"]
}

x = person("X")

print(x)

grammar = tracery.Grammar(symbols) # create a grammar object from the rules
grammar.add_modifiers(base_english) # add pre-programmed modifiers

poo


TypeError: cannot create 'builtin_function_or_method' instances

In [97]:
# basic classes

class Dog:
    kind = 'canine'
    
    def __init__(self, name):
        self.name = name    

print(Dog.kind) # any flipping dog

r = Dog('Rex')
print(r.name, r.kind)
f = Dog('Fido')
print(f.name, f.kind)

canine
Rex canine
Fido canine


In [119]:
# so, let's try this with a town. A new grammar for each company!


# YES THIS IS RESTATING LOADS OF STUFF I KNOW

def loadData():
    with open('corpora/townprefixes.txt','r') as f:
        townprefixes = [line.strip() for line in f]
    with open('corpora/townsuffixes.txt','r') as f:
        townsuffixes = [line.strip() for line in f]
    with open('corpora/monopolystreets.txt','r') as f:
        street = [line.strip() for line in f]

    # print("prefixes = ",townprefixes)
    # print("suffixes =",townsuffixes)

rules = {
    "name": ["butcher","baker","candlestick maker"],
    "address": "#number# #street.capitalize#, #town.capitalize#, #zipcode#",
    "number": ["#d0#","#d0##d#","#d0##d##d#","#d0##d##d#","#d0##d##d#","#d0##d##d#","#d0##d##d##d#","#d0##d##d##d#","#d0##d##d##d#","#d0##d##d##d#","#d0##d##d##d#","#d0##d##d##d#","#d0##d##d##d#","#d0##d##d##d#","#d0##d##d##d#"],
    "street": street,
    "town": "#prefix.capitalize##suffix#",
    "prefix": townprefixes,
    "suffix": townsuffixes,
    "zipcode": "#d##d##d##d##d#",
    "d":["0","1","2","3","4","5","6","7","8","9"],
    "d0":["1","2","3","4","5","6","7","8","9"]
}

loadData()
grammar = tracery.Grammar(rules) # create a grammar object from the rules
grammar.add_modifiers(base_english) # add pre-programmed modifiers

class Business:
    kind = 'business'
    def __init__(self,name):
        self.name = grammar.flatten("#name.capitalize#")
        self.town = grammar.flatten("#town#")
        
        
print(Business.kind)

a = Business('Name')
print (a.kind, a.name, a.town)

business
business Butcher Kilochester


In [133]:
# ok, so that works...now let's define categories, and create a few new businesses per category


rules = {
    "cat": ["butchers","bakers","accountants","hitmen"], #to expand later
}

grammar = tracery.Grammar(rules)
grammar.add_modifiers(base_english)


class Category:
    kind = 'category'
    def __init__(self,name):
        self.name = grammar.flatten("#cat.capitalize#")
        
a = Category('hm')
print(a.name)

Hitmen


# Mottoes

Companies in the old Yellow Pages have great mottoes, e.g.

    The {biggest/best/oldest/rarest/most sought-after} {business category/prices/selection} {in/near/{north/south/east/west/just outside} of} {town/county}{!/!!/!!!}

or 

    We put the _x_ in _y_ (where _y_ is a word associated with the business type)

or 

    Home of the {category} {doctor/specialists/repairers/practitioners}
    
or

    You've seen the rest, now find the best!
    
or

    Complete systems - one year warranty
    
or 

    {list of related services, with • separators}
    
or 

    From {one thing related to category} to {another thing related to category}
    
or 

    FREE ESTIMATES and NO PAYMENT UPFRONT
    INTEREST-FREE CREDIT

(perhaps a category of "benefits"?)

In [140]:
# the biggest selection in warburton!

loadData()
rules = {
    "motto": ["The #superlative# #thing# #located# #town#"],
    "superlative": ["biggest","best","oldest","rarest","most sought-after","nicest","prettiest"],
    "thing": ["prices","selection","collection","range","budget option"],
    "located": ["in","near","#dir# of"],
    "dir": ["north","south","east","west","just outside"],
    "town": "#prefix.capitalize##suffix#",
    "prefix": townprefixes,
    "suffix": townsuffixes
}

grammar = tracery.Grammar(rules) # create a grammar object from the rules
grammar.add_modifiers(base_english) # add pre-programmed modifiers

for i in range(30):
    print (grammar.flatten("#motto#")) # and flatten, starting with origin rule

The biggest prices near Quebecton
The nicest selection south of Foxtrotside
The best prices north of Romeoster
The rarest prices in Oscarview
The best prices in Limafield
The most sought-after collection in Limafield
The biggest prices in Zuluburn
The biggest selection near Deltabridge
The nicest selection east of Tangoland
The oldest selection in Limaton
The biggest budget option just outside of Xrayston
The most sought-after budget option near Limaport
The best budget option near Deltaford
The oldest selection in Deltadam
The oldest range near Kiloview
The biggest collection north of Whiskeyford
The biggest range east of Zuluton
The nicest budget option in Indiachester
The prettiest selection just outside of Xrayland
The prettiest range in Zuluville
The best selection near Sierrason
The oldest collection west of Deltaston
The biggest collection south of Golfford
The oldest selection just outside of Quebecstone
The nicest prices near Limaster
The oldest collection south of Kilobridge


In [303]:
# the biggest selection in warburton!

with open('corpora/words_alpha.txt','r') as f:
    stupid = [line.strip() for line in f]
with open('corpora/we_put_the_x_in_y_old.txt','r') as f:
    weputthe = [line.strip() for line in f]

rules = {
    "motto": ["#tellem#","#weputthexiny#","The #superlative# #thing# #located# #town#","#owned.capitalize#","#stuff#","#directions#","#youlike#","#youlike# #directions#","#localpromo#"],
    "owned":["#division.a# of #something.capitalize# #inc#","#division.a# of #something.capitalize# #inc.capitalize#","Part of the #something.capitalize# #inc#"],
    "owned2":["#division.a# of #acronym.capitalize# #inc#","#division.a# of #acronym.capitalize# #inc.uppercase#","Part of the #acronym.capitalize# #inc#"],
    "acronym": ["#letter.uppercase#.#letter.uppercase#.","#letter.uppercase#.#letter.uppercase#.#letter.uppercase#.","#letter.uppercase##letter.uppercase##letter.uppercase#","#letter.uppercase##letter.uppercase##letter.uppercase##letter.uppercase#","#letter.uppercase##letter.uppercase##letter.uppercase##letter.uppercase##letter.uppercase#","#letter.uppercase#-#letter.uppercase#-#letter.uppercase#-#letter.uppercase#"],
    "inc": ["Family","Network","Network of Companies","LLC","PLC","L.L.C."],
    "something": stupid,
    "division":["Proud Member","Founding Member"],
    "superlative": ["biggest","best","oldest","rarest","most sought-after","nicest","prettiest"],
    "thing": ["prices","selection","collection","range","budget option","#size# selection"],
    "size": ["mid-range","large-scale","huge","budget","high budget","upscale"],
    "located": ["in","near","#dir# of"],
    "dir": ["north","south","east","west","just outside"],
    "town": "#prefix.capitalize##suffix#",
    "prefix": townprefixes,
    "suffix": townsuffixes,
    "stuff": ["#something.capitalize#, #something.capitalize#, & #something.capitalize#!","#something.capitalize# • #something.capitalize# • #something.capitalize#","#wevegot# #something.capitalize#!"],
    "wevegot": ["We've got","You'll love our","Why not try","Take a look at our","Relax with","Prod our"],
    "directions":["#action# #dir# at #town#","#action# #dir# at #place#, #action# for #distance# #measurement#","#place.capitalize#: #action# #dir# at #town#, #action# #dir# at #town#, #action# #dir# at #town#"],
    "place":["#town#","Junction #d0##d#","Interstate #d0##d#","the #something.capitalize#"],
    "action":["Turn","Continue Straight","Continue","Drive"],
    "distance": ["#d0#","#d0##d#"],
    "measurement":["miles","feet"],
    "d":["0","1","2","3","4","5","6","7","8","9"],
    "d0":["1","2","3","4","5","6","7","8","9"],
    "youlike":["#something.capitalize# #timespan#!","You like #stuff.capitalize#? We've got it!","Have you ever wanted #something.capitalize#?","Have you ever wanted #something.capitalize#? We have #something.capitalize#!","Dreaming of #something.capitalize#?!","Why not try #something.capitalize# #timespan#?"],
    "timespan":["now","tomorrow","today","right now","immediately","the next chance you get"],
    "weputthe":["We put the #something# in #something.s#"],
    "tellem":["#tell# #firstname# sent you!","Recommended by #amazingjob# #firstname.capitalize# #lastname.capitalize#"],
    "tell":["Tell them","Tell 'em","Just say"],
    "amazingjob":["#qualifier# #job#"],
    "qualifier":["top","local celebrity","well-known","your favourite","family favourite","the one and only","phenomenal","the best","excellent","mediocre"],
    "job":["chef","TV host","Psychic","carpenter","denstist","orthodontist"],
    "firstname":["John","Mary","Frank","Anne"],
    "lastname":["Hutchins","Bandage","Cabbage","Smith"],
    "weputthexiny":["#weputthe#!","#weputthe#!!!","#weputthe#"],
    "weputthe":weputthe,
    "localpromo":["Hear our advert on #localstation#","You might have heard about us on #localstation#","Proud sponsors of #localstation#"],
    "localstation":["#something.capitalize# #d0##d#.#d0# FM","#qualifier# local station #something.capitalize# #d0##d#.#d0# FM","1#d##d#.#d0# FM"]
}

grammar = tracery.Grammar(rules) # create a grammar object from the rules
grammar.add_modifiers(base_english) # add pre-programmed modifiers

for i in range(100):
    print (grammar.flatten("#motto#")) # and flatten, starting with origin rule

We've got Lupinous!
Recommended by phenomenal denstist Frank Smith
We put the "tor" in "ruddervator"
Interstate 57: Continue Straight just outside at Romeotown, Drive north at Whiskeyview, Continue north at Kilochester
Tell 'em Mary sent you!
We put the "nt" in "adherant"!
A Proud Member of Heretoga L.L.C.
We put the "hing" in "electroetching"!!!
Proud sponsors of 172.4 FM
Recommended by the best orthodontist Anne Cabbage
We put the "naturalistic" in "supranaturalistic"!
Dreaming of Estovers?!
Why not try Tetraptych tomorrow?
A Founding Member of Piedroit PLC
We put the "ignitor" in "signitor"!!!
Turn north at Deltadam, Continue for 2 feet
The prettiest selection near Echoview
Why not try Delating today? Turn just outside at Tangostone, Continue Straight for 95 feet
We've got Desponsate!
The nicest mid-range selection in Tangofield
Part of the Protozoean Network of Companies
The rarest collection near Zuluville
Coelect • Mustelinous • Toty
Junction 50: Drive west at Hoteltown, Continue

In [283]:
# hear our ad on 99.7 Tabaloca FM! read about us in the local news!

hi


In [308]:
# Storing variables, from tutorial

rules = {
    "name": ["Arjun","Yuuma","Darcy","Mia","Chiaki","Izzi","Azra","Lina"],
    "animal": ["unicorn","raven","sparrow","scorpion","coyote","eagle","owl","lizard","zebra","duck","kitten"],
    "occupationBase": ["wizard","witch","detective","ballerina","criminal","pirate","lumberjack","spy","doctor","scientist","captain","priest"],
    "occupationMod": ["occult ","space ","professional ","gentleman ","erotic ","time ","cyber","paleo","techno","super"],
    "strange": ["mysterious","portentous","enchanting","strange","eerie"],
    "tale": ["story","saga","tale","legend"],
    "occupation": ["#occupationMod##occupationBase#"],
    "mood": ["vexed","indignant","impassioned","wistful","astute","courteous"],
    "setPronouns": ["[heroThey:they][heroThem:them][heroTheir:their][heroTheirs:theirs]","[heroThey:she][heroThem:her][heroTheir:her][heroTheirs:hers]","[heroThey:he][heroThem:him][heroTheir:his][heroTheirs:his]"],
    "setSailForAdventure": ["set sail for adventure","left #heroTheir# home","set out for adventure","went to seek #heroTheir# forture"],
    "setCharacter": ["[#setPronouns#][hero:#name#][heroJob:#occupation#]"],
    "openBook": ["An old #occupation# told #hero# a story. 'Listen well' she said to #hero#, 'to this #strange# #tale#. ' #origin#'","#hero# went home.","#hero# found an ancient book and opened it.  As #hero# read, the book told #strange.a# #tale#: #origin#"],
    "story": ["#hero# the #heroJob# #setSailForAdventure#. #openBook#"],
    "origin": ["Once upon a time, #[#setCharacter#]story#"]
}

grammar = tracery.Grammar(rules) # create a grammar object from the rules
grammar.add_modifiers(base_english) # add pre-programmed modifiers

for i in range(1):
    print (grammar.flatten("#origin#")) # and flatten, starting with origin rule

Once upon a time, Yuuma the gentleman witch went to seek his forture. An old space priest told Yuuma a story. 'Listen well' she said to Yuuma, 'to this strange story. ' Once upon a time, Mia the cyberwitch went to seek his forture. An old erotic pirate told Mia a story. 'Listen well' she said to Mia, 'to this mysterious story. ' Once upon a time, Darcy the cyberscientist went to seek his forture. Darcy found an ancient book and opened it.  As Darcy read, the book told a mysterious legend: Once upon a time, Darcy the superdoctor set out for adventure. An old gentleman scientist told Darcy a story. 'Listen well' she said to Darcy, 'to this enchanting story. ' Once upon a time, Azra the supercriminal set out for adventure. Azra went home.'''


In [58]:
# Storing variables, my ones this time

rules = {
    "this":["The company is called [#listing#]#company#. Phone no. #phone#, address: #address#. Again, the company is called [#setcompany#]#company#. Phone no. #phone#, address: #address#."],
    "listing":["[company:#setname#],[motto:#setmotto#],[address:#setaddress#],[phone:#setphone#]"],
    "setname":["Bill's Flowers","Tracy's Boutique","Frank's Coffee"],
    "setmotto":["At your service.","Pleased to help.","Look at our stuff."],
    "setaddress":["123 Street Street."]
}

grammar = tracery.Grammar(rules) # create a grammar object from the rules
grammar.add_modifiers(base_english) # add pre-programmed modifiers

for i in range(1):
    print (grammar.flatten("#this#")) # and flatten, starting with origin rule

The company is called Frank's Coffee. Phone no. ((setphone)), address: 123 Street Street.. Again, the company is called Frank's Coffee. Phone no. ((setphone)), address: 123 Street Street..


In [339]:
# the biggest selection in warburton!

with open('corpora/words_alpha.txt','r') as f:
    stupid = [line.strip() for line in f]
with open('corpora/we_put_the_x_in_y_old.txt','r') as f:
    weputthe = [line.strip() for line in f]    
with open('corpora/townprefixes.txt','r') as f:
    townprefixes = [line.strip() for line in f]
with open('corpora/townsuffixes.txt','r') as f:
    townsuffixes = [line.strip() for line in f]
with open('corpora/streetnames.txt','r') as f:
    street = [line.strip() for line in f]
with open('corpora/words_alpha.txt','r') as f:
    words = [line.strip() for line in f]
with open('corpora/top_us_surnames.txt','r') as f:
    surnames = [line.strip() for line in f]
with open('corpora/businesstypes_rough.txt','r') as f:
    categories = [line.strip() for line in f] # business types taken from wikipedia. this should change soon!
with open('corpora/top_5494_names_us_1990.txt','r') as f:
    firstnames = [line.strip() for line in f]
nltk.download('names')
from nltk.corpus import names
for i in range(len(names.words())):
    print(names.words()[i])
    firstnames.append(names.words()[i])




    
rules = {
    "listing":["[#companyinfo#]#name.capitalize#\n\"#motto#\"\n✉ #address#\n☎ #phone#\n\n"],
    
    # set company info
    "companyinfo":["[town:#settown#],[category:#setcategory#],[name:#setname#],[address:#setaddress#],[phone:#setphone#],[motto:#setmotto#]"],
    
    # town
    "settown":"#prefix.capitalize##suffix#",
    "prefix": townprefixes,
    "suffix": townsuffixes,
    
    # category
    "setcategory":categories,
    
    
    # company name
    "setname":["#something.capitalize# #category.s.capitalizeAll#","#initials# #category.capitalizeAll#","#initials# #category.capitalizeAll.s#","#town# #category.capitalizeAll#","#firstname#'s #category.capitalizeAll#","#firstname#'s #category.capitalizeAll.s#","#initials# #surname# #and# #category.capitalizeAll#"],
    "initials":["#l.capitalize#.","#l.capitalize#.#l.capitalize#.","#l.capitalize##l.capitalize#","#firstname.capitalize# #l.capitalize#."],
    "l":["a","b","c","d","e","f","g","h","i","j","k","l","m","n","o","p","q","r","s","t","u","v","w","x","y","z"],
    "firstname":firstnames,
    "surname":surnames,
    "and":["& Sons","& Co","and company","Incorporated"],

    
    # address
    "setaddress": "#streetname.capitalize#, #town.capitalize#",
    "number": ["#d0#","#d0##d#","#d0##d##d#","#d0##d##d#","#d0##d##d#","#d0##d##d#","#d0##d##d##d#","#d0##d##d##d#","#d0##d##d##d#","#d0##d##d##d#","#d0##d##d##d#","#d0##d##d##d#","#d0##d##d##d#","#d0##d##d##d#","#d0##d##d##d#"],
    "streetname":["#number# #street# #streettype#","#number# #street# #streettype#","#street# & #street#"],
    "streettype":["Avenue","Street","Road","Lane","Parkway","St","Ave"],
    "street": street,
    "town": "#prefix.capitalize##suffix#",
    "prefix": townprefixes,
    "suffix": townsuffixes,
    "zipcode": "#d##d##d##d##d#",
    "d":["0","1","2","3","4","5","6","7","8","9"],
    "d0":["1","2","3","4","5","6","7","8","9"],
    
    # phone number
    "setphone":["#d0##d##d#-#d##d##d##d#"],

    
    # motto
    "setmotto": ["#tellem#","#weputthexiny#","#weputthexiny#","The #superlative# #thing# #located# #town#","#owned.capitalize#","#stuff#","#directions#","#youlike#","#youlike# \n#directions#","#localpromo#"],
    "owned":["#division.a# of #something.capitalize# #inc#","#division.a# of #something.capitalize# #inc.capitalize#","Part of the #something.capitalize# #inc#"],
    "owned2":["#division.a# of #acronym.capitalize# #inc#","#division.a# of #acronym.capitalize# #inc.uppercase#","Part of the #acronym.capitalize# #inc#"],
    "acronym": ["#letter.uppercase#.#letter.uppercase#.","#letter.uppercase#.#letter.uppercase#.#letter.uppercase#.","#letter.uppercase##letter.uppercase##letter.uppercase#","#letter.uppercase##letter.uppercase##letter.uppercase##letter.uppercase#","#letter.uppercase##letter.uppercase##letter.uppercase##letter.uppercase##letter.uppercase#","#letter.uppercase#-#letter.uppercase#-#letter.uppercase#-#letter.uppercase#"],
    "inc": ["Family","Network","Network of Companies","LLC","PLC","L.L.C."],
    "something": stupid,
    "division":["Proud Member","Founding Member"],
    "superlative": ["biggest","best","oldest","rarest","most sought-after","nicest","prettiest"],
    "thing": ["prices","selection","collection","range","budget option","#size# selection"],
    "size": ["mid-range","large-scale","huge","budget","high budget","upscale"],
    "located": ["in","near","#dir# of"],
    "dir": ["north","south","east","west","just outside"],
    "stuff": ["#something.capitalize#, #something.capitalize#, & #something.capitalize#!","#something.capitalize# • #something.capitalize# • #something.capitalize#","#wevegot# #something.capitalize#!"],
    "wevegot": ["We've got","You'll love our","Why not try","Take a look at our","Relax with","Prod our"],
    "directions":["#action# #dir# at #town#","#action# #dir# at #place#, #action# for #distance# #measurement#","#place.capitalize#: #action# #dir# at #town#, #action# #dir# at #town#, #action# #dir# at #town#"],
    "place":["#town#","Junction #d0##d#","Interstate #d0##d#","the #something.capitalize#"],
    "action":["Turn","Continue Straight","Continue","Drive"],
    "distance": ["#d0#","#d0##d#"],
    "measurement":["miles","feet"],
    "youlike":["#something.capitalize# #timespan#!","You like #stuff.capitalize#? We've got it!","Have you ever wanted #something.capitalize#?","Have you ever wanted #something.capitalize#? We have #something.capitalize#!","Dreaming of #something.capitalize#?!","Why not try #something.capitalize# #timespan#?"],
    "timespan":["now","tomorrow","today","right now","immediately","the next chance you get"],
    "weputthe":["We put the #something# in #something.s#"],
    "tell":["Tell them","Tell 'em","Just say"],
    "amazingjob":["#qualifier# #job#"],
    "qualifier":["top","local celebrity","well-known","your favourite","your friend and mine,","family favourite","the one and only","phenomenal","the best","excellent","mediocre"],
    "job":["chef","TV host","Psychic","carpenter","denstist","orthodontist"],
    "tellem":["#tell# #firstname# sent you!","Recommended by #amazingjob# #firstname.capitalize# #surname.capitalize#"],
    "tell":["Tell them","Tell 'em","Just say"],

    
    
    "weputthexiny":["#weputthe#!","#weputthe#!!!","#weputthe#"],
    "weputthe":weputthe,
    "localpromo":["Hear our advert on #localstation#","You might have heard about us on #localstation#","Proud sponsors of #localstation#"],
    "localstation":["#something.capitalize# #d0##d#.#d0# FM","#qualifier# local station #something.capitalize# #d0##d#.#d0# FM","1#d##d#.#d0# FM"]
}

grammar = tracery.Grammar(rules) # create a grammar object from the rules
grammar.add_modifiers(base_english) # add pre-programmed modifiers

for i in range(10000):
    print (grammar.flatten("#listing#")) # and flatten, starting with origin rule


[nltk_data] Downloading package names to /Users/ompalmer/nltk_data...
[nltk_data]   Package names is already up-to-date!


Abagael
Abagail
Abbe
Abbey
Abbi
Abbie
Abby
Abigael
Abigail
Abigale
Abra
Acacia
Ada
Adah
Adaline
Adara
Addie
Addis
Adel
Adela
Adelaide
Adele
Adelice
Adelina
Adelind
Adeline
Adella
Adelle
Adena
Adey
Adi
Adiana
Adina
Adora
Adore
Adoree
Adorne
Adrea
Adria
Adriaens
Adrian
Adriana
Adriane
Adrianna
Adrianne
Adrien
Adriena
Adrienne
Aeriel
Aeriela
Aeriell
Ag
Agace
Agata
Agatha
Agathe
Aggi
Aggie
Aggy
Agna
Agnella
Agnes
Agnese
Agnesse
Agneta
Agnola
Agretha
Aida
Aidan
Aigneis
Aila
Aile
Ailee
Aileen
Ailene
Ailey
Aili
Ailina
Ailyn
Aime
Aimee
Aimil
Aina
Aindrea
Ainslee
Ainsley
Ainslie
Ajay
Alaine
Alameda
Alana
Alanah
Alane
Alanna
Alayne
Alberta
Albertina
Albertine
Albina
Alecia
Aleda
Aleece
Aleecia
Aleen
Alejandra
Alejandrina
Alena
Alene
Alessandra
Aleta
Alethea
Alex
Alexa
Alexandra
Alexandrina
Alexi
Alexia
Alexina
Alexine
Alexis
Alfie
Alfreda
Ali
Alia
Alica
Alice
Alicea
Alicia
Alida
Alidia
Alina
Aline
Alis
Alisa
Alisha
Alison
Alissa
Alisun
Alix
Aliza
Alla
Alleen
Allegra
Allene
Alli
Allianora
Allie
A

Cornelle
Cornie
Corny
Correna
Correy
Corri
Corrianne
Corrie
Corrina
Corrine
Corrinne
Corry
Cortney
Cory
Cosetta
Cosette
Courtenay
Courtney
Cresa
Cris
Crissie
Crissy
Crista
Cristabel
Cristal
Cristen
Cristi
Cristie
Cristin
Cristina
Cristine
Cristionna
Cristy
Crysta
Crystal
Crystie
Cyb
Cybal
Cybel
Cybelle
Cybil
Cybill
Cyndi
Cyndy
Cynthea
Cynthia
Cynthie
Cynthy
Dacey
Dacia
Dacie
Dacy
Dael
Daffi
Daffie
Daffy
Dafna
Dagmar
Dahlia
Daile
Daisey
Daisi
Daisie
Daisy
Dale
Dalenna
Dalia
Dalila
Dallas
Daloris
Damara
Damaris
Damita
Dana
Danell
Danella
Danelle
Danette
Dani
Dania
Danica
Danice
Daniel
Daniela
Daniele
Daniella
Danielle
Danika
Danila
Danit
Danita
Danna
Danni
Dannie
Danny
Dannye
Danya
Danyelle
Danyette
Daphene
Daphna
Daphne
Dara
Darb
Darbie
Darby
Darcee
Darcey
Darci
Darcie
Darcy
Darda
Dareen
Darell
Darelle
Dari
Daria
Darice
Darla
Darleen
Darlene
Darline
Darryl
Darsey
Darsie
Darya
Daryl
Daryn
Dasha
Dasi
Dasie
Dasya
Datha
Daune
Daveen
Daveta
Davida
Davina
Davine
Davita
Dawn
Dawna
Dayle
Dayna


Jacenta
Jacinda
Jacinta
Jacintha
Jacinthe
Jackelyn
Jacki
Jackie
Jacklin
Jacklyn
Jackquelin
Jackqueline
Jacky
Jaclin
Jaclyn
Jacquelin
Jacqueline
Jacquelyn
Jacquelynn
Jacquenetta
Jacquenette
Jacquetta
Jacquette
Jacqui
Jacquie
Jacynth
Jada
Jade
Jaime
Jaimie
Jaine
Jaleh
Jami
Jamie
Jamima
Jammie
Jan
Jana
Janaya
Janaye
Jandy
Jane
Janean
Janeczka
Janeen
Janel
Janela
Janella
Janelle
Janene
Janenna
Janessa
Janet
Janeta
Janetta
Janette
Janeva
Janey
Jania
Janice
Janie
Janifer
Janina
Janine
Janis
Janith
Janka
Janna
Jannel
Jannelle
Janot
Jany
Jaquelin
Jaquelyn
Jaquenetta
Jaquenette
Jaquith
Jasmin
Jasmina
Jasmine
Jayme
Jaymee
Jayne
Jaynell
Jazmin
Jean
Jeana
Jeane
Jeanelle
Jeanette
Jeanie
Jeanine
Jeanna
Jeanne
Jeannette
Jeannie
Jeannine
Jehanna
Jelene
Jemie
Jemima
Jemimah
Jemmie
Jemmy
Jen
Jena
Jenda
Jenelle
Jenette
Jeni
Jenica
Jeniece
Jenifer
Jeniffer
Jenilee
Jenine
Jenn
Jenna
Jennee
Jennette
Jenni
Jennica
Jennie
Jennifer
Jennilee
Jennine
Jenny
Jeraldine
Jeralee
Jere
Jeri
Jermaine
Jerrie
Jerrilee
Jer

Max
Maxi
Maxie
Maxine
Maxy
May
Maya
Maybelle
Mayda
Maye
Mead
Meade
Meagan
Meaghan
Meara
Mechelle
Meg
Megan
Megen
Meggan
Meggi
Meggie
Meggy
Meghan
Meghann
Mehetabel
Mei
Meira
Mel
Mela
Melamie
Melania
Melanie
Melantha
Melany
Melba
Melesa
Melessa
Melicent
Melina
Melinda
Melinde
Melisa
Melisande
Melisandra
Melisenda
Melisent
Melissa
Melisse
Melita
Melitta
Mella
Melli
Mellicent
Mellie
Mellisa
Mellisent
Mellissa
Melloney
Melly
Melodee
Melodie
Melody
Melonie
Melony
Melosa
Melva
Mercedes
Merci
Mercie
Mercy
Meredith
Meredithe
Meridel
Meridith
Meriel
Merilee
Merilyn
Meris
Merissa
Merl
Merla
Merle
Merlina
Merline
Merna
Merola
Merralee
Merridie
Merrie
Merrielle
Merrile
Merrilee
Merrili
Merrill
Merrily
Merry
Mersey
Meryl
Meta
Mia
Micaela
Michaela
Michaelina
Michaeline
Michaella
Michal
Michel
Michele
Michelina
Micheline
Michell
Michelle
Micki
Mickie
Micky
Midge
Mignon
Mignonne
Miguela
Miguelita
Mikako
Mildred
Mildrid
Milena
Milicent
Milissent
Milka
Milli
Millicent
Millie
Millisent
Milly
Milzie
Mimi


...


G.W. Script Coordinator
"Just say Humphrey sent you!"
✉ 36 Center Avenue, Juliettchester
☎ 907-2196


GH Database Administrator
"We put the "aim" in "counterclaim"!"
✉ 945 Fenchurch Ave, Golfville
☎ 422-4681


Edwina's Music
"Catchie • Hutching • Purblind"
✉ 373 County Line Lane, Foxtrotside
☎ 793-1558


PK Yarn Engineering"
"Politicaster, Reconcentration, & Tribracteate!"
✉ 3 Narragansett Parkway, Tangoland
☎ 137-9741


Chris's Computer Analyst
"Dreaming of Undiademed?!"
✉ Liverpool & Mountain View, Victorster
☎ 203-5388


Vada's Biologists
"Turn east at the Unturbid, Drive for 5 miles"
✉ 2 Columbine St, Echoson
☎ 488-1611


Victorland Ghostwriter
"Have you ever wanted Frigorifico? We have Dysarthrosis!"
✉ 7348 Cottonwood Ave, Victorland
☎ 737-3187


A.A. Electronic Equipment Maintainers
"Recommended by top Psychic Isiah White"
✉ King’s Cross & Spruce, Whiskeyton
☎ 572-4207


T. Scrivener
"Have you ever wanted Trains? We have Remounted! 
Junction 61: Continue just outside at Echoches


EK Chemical Engineer
"Hear our advert on 175.1 FM"
✉ 966 Hickory Lane, Juliettville
☎ 954-3354


Tore's Writers
"We put the "redo" in "tenthredo"!!!"
✉ 4th & Kukui, Yankeeville
☎ 396-6621


EH Bush and company Director
"Intravenous • Cd • Dagaba"
✉ 6725 Smith Street, Whiskeyland
☎ 123-5725


Dromaeus Ophthalmologists
"Have you ever wanted Bordar? 
Continue Straight east at Interstate 33, Turn for 1 feet"
✉ 6th & Hemlock, Zuluville
☎ 399-7766


Xrayport Chief Strategy Officer
"The biggest prices near Xrayport"
✉ 5609 Pentonville Parkway, Xrayport
☎ 590-0617


Vergil's Chief People Officer
"Why not try Unclinched immediately? 
Interstate 87: Turn west at Novemberdam, Continue Straight south at Novemberdam, Turn just outside at Novemberdam"
✉ 155 1st Avenue, Novemberdam
☎ 490-5307


Necole's Cryptographic Engineerings
"Proud sponsors of 106.7 FM"
✉ Magnolia & Church, Mikeford
☎ 174-2930


Gaincome Boilermans
"We put the "ess" in "warlikeness"!"
✉ 328 Kahili Road, Juliettport
☎ 742-2774



Indiastone Chief Services Officer
"Continue Straight south at Indiastone"
✉ 5494 Delaware Ave, Indiastone
☎ 200-1696


Sasha's Senior Station Master
"Effectuation, Meckelectomy, & Chinbone!"
✉ 7927 Hemlock Road, Foxtrotdam
☎ 675-0616


A.M. Electrical Engineerings
"Hear our advert on 120.6 FM"
✉ 8995 Wood Avenue, Sierrastone
☎ 465-6575


Stacie's Foreman
"You might have heard about us on 116.7 FM"
✉ Hillside & Cypress, Yankeeview
☎ 998-8241


Merrick's Toolses
"Tell them Chase sent you!"
✉ 818 Wilson Street, Limaston
☎ 543-0079


Felicio's Janitors
"Tell them Denyse sent you!"
✉ 2750 Marylebone Ave, Alfaster
☎ 149-0179


Averil's Illusionist
"We put the "ting" in "uningratiating"!"
✉ 989 Highland St, Romeoster
☎ 546-1535


Sheena's Clown
"We put the "ian" in "pilatian"!"
✉ 3328 Main Ave, Hotelland
☎ 859-7207


Q. Security Engineer
"We put the "ne" in "acervuline"!"
✉ Kukui & Fleet, Papaview
☎ 672-0598


Chieko's Software Engineering
"Proud sponsors of 178.4 FM"
✉ 241 Aspen Ave, Oscarpo

Kin's Deputy Station Masters
"Why not try Inamoratas tomorrow? 
Continue Straight north at Junction 39, Drive for 5 feet"
✉ 2383 Fleet Street, Romeobridge
☎ 815-8439


Subhedral Hospital-Related Productses
"Have you ever wanted Redemptionless? We have Hagmane! 
Continue just outside at Hotelster, Continue for 8 feet"
✉ 8096 23rd St, Hotelster
☎ 195-6401


Gruntingly Freelancers
"Part of the Propriatory Network"
✉ 2341 Mountain View St, Novemberview
☎ 699-1316


J.Z. Pointsman
"The oldest budget selection in Charlieburn"
✉ 264 12th Ave, Charlieburn
☎ 339-6054


Xrayston Railway Engineering
"Recommended by excellent orthodontist Joanna Corona"
✉ 4314 Magnolia Street, Xrayston
☎ 203-1500


V. Instrumentation Engineerings
"A Proud Member of Plical LLC"
✉ 2911 Strand Street, Oscarston
☎ 215-7881


Terese I. Measurements
"You'll love our Garters!"
✉ 8627 5th Road, Kiloster
☎ 126-6731


Ethelene's Project Managements
"Hear our advert on Arf 45.7 FM"
✉ 3057 Strand Avenue, Quebecson
☎ 598-1233


Oinked Physical Therapists
"Continue Straight just outside at Limabridge, Drive for 75 miles"
✉ 9626 Pall Ave, Limabridge
☎ 168-4609


Q.I. Anesthesiologies
"Just say Orelia sent you!"
✉ Pine & Columbine, Echoston
☎ 263-9403


QW Phlebotomists
"We put the "ally" in "rhombohedrally""
✉ Cherry & Euston, Julietttown
☎ 315-1509


IW Chief Research Officer
"Recommended by the best TV host Jaime Carey"
✉ 7584 Dogwood Avenue, Papabridge
☎ 654-1237


E.J. Fleming & Sons Iron Turtle
"Proud sponsors of mediocre local station Misrule 81.1 FM"
✉ 8228 West Parkway, Charlieland
☎ 236-7346


Unexplicative Dance Scholars
"A Founding Member of Fornicated Family"
✉ 178 Lehua Avenue, Hotelside
☎ 494-4975


Michelle's Junior Station Master
"We put the "rs" in "undertakers""
✉ 5 Elm Lane, Hotelport
☎ 489-1375


Juliann O. Filling Station Attendant
"Dreaming of Echeveria?!"
✉ 333 9th Lane, Alfaland
☎ 396-4569


Robin's Teletraffic Engineerings
"Turn west at Romeochester"
✉ 2 Lincoln Road, Romeochester
☎ 692

# update 

OK, so the above now creates businesses with names, mottoes, addresses, and phone numbers. In order to make this more interesting, the directory should begin devising new types of business: taking verbs and nouns and modifying them to reach new hybrid forms company. I'd like to get to a stage where this type of business category could emerge:


- Horse Splitting
- Forensic Economics Distillation
- Nanocryptography
- Future Endorsements
- Bifurbic Transportation
- Pathological Introductions

There are obviously generic prepositions which can modify nearly any category, e.g.

- nano
- crypto
- pseudo
- sci
- biological
- endopic
- forensic

Then there are the middle sections, the real subject. I think these could be nouns or adjectives (these taken from random word sample from wordnet):

- cholanic 
- nocuous 
- sarcilis 
- proceritic 
- sketchist 
- zygotene 
- precondemnation 
- Gregarinoidea 
- pearceite 
- gurgly 
- superterrestrial 
- oblanceolate 
- uncircumcisedness 
- compromising 
- presenced 
- dichroic 
- supersensuous 
- sunbreak 
- amygdalate 
- edulcoration

Note that these should all be modified to be present tense, -ing, -age, -ion, -al, that sort of word. 

Then there are the endings:

- Services
- Brokers
- Futures
- Solutions

Sometimes these have modifiers, e.g.:

- Financial Solutions
- Regional Brokers

(can this be a simple adjective?)

Plus there are different structures:

- noun verb (ing format) (in [Nodebox](https://www.nodebox.net/code/index.php/Linguistics#verb_conjugation) this is via the function verb.present_participle(word))...actually, let's just do this with NLTK!
- modifier-verb (y format)

NOTE that the library I'll use here is NLTK which seems to be able to do anything modifier-y with words.

In [98]:
# let's install NLTK
!pip3 install numpy # install numpy to start
!pip3 install nltk # then nltk
import nltk
nltk.download('punkt') # this needs to happen at some point
nltk.download('averaged_perceptron_tagger') # and this
nltk.download('maxent_ne_chunker') # and this
nltk.download('words') # and this
nltk.download('wordnet') # and this

[nltk_data] Downloading package punkt to /Users/ompalmer/nltk_data...
[nltk_data]   Package punkt is already up-to-date!
[nltk_data] Downloading package averaged_perceptron_tagger to
[nltk_data]     /Users/ompalmer/nltk_data...
[nltk_data]   Package averaged_perceptron_tagger is already up-to-
[nltk_data]       date!
[nltk_data] Downloading package maxent_ne_chunker to
[nltk_data]     /Users/ompalmer/nltk_data...
[nltk_data]   Package maxent_ne_chunker is already up-to-date!
[nltk_data] Downloading package words to /Users/ompalmer/nltk_data...
[nltk_data]   Package words is already up-to-date!
[nltk_data] Downloading package wordnet to
[nltk_data]     /Users/ompalmer/nltk_data...
[nltk_data]   Unzipping corpora/wordnet.zip.


True

In [95]:
# nltk tasting...demos from website https://www.nltk.org/index.html

sentence = """At eight o'clock on Thursday morning
... Arthur didn't feel very good."""

tokens = nltk.word_tokenize(sentence)
print(tokens)

tagged = nltk.pos_tag(tokens)
print(tagged)

entities = nltk.chunk.ne_chunk(tagged)
print(entities)

['At', 'eight', "o'clock", 'on', 'Thursday', 'morning', '...', 'Arthur', 'did', "n't", 'feel', 'very', 'good', '.']
[('At', 'IN'), ('eight', 'CD'), ("o'clock", 'NN'), ('on', 'IN'), ('Thursday', 'NNP'), ('morning', 'NN'), ('...', ':'), ('Arthur', 'NNP'), ('did', 'VBD'), ("n't", 'RB'), ('feel', 'VB'), ('very', 'RB'), ('good', 'JJ'), ('.', '.')]
(S
  At/IN
  eight/CD
  o'clock/NN
  on/IN
  Thursday/NNP
  morning/NN
  .../:
  (PERSON Arthur/NNP)
  did/VBD
  n't/RB
  feel/VB
  very/RB
  good/JJ
  ./.)


In [113]:
from nltk.corpus import wordnet
syns = wordnet.synsets("test") 
print(syns[0].lemmas()[0].name())
print(syns[0].examples())

synonyms = [] 
antonyms = [] 
  
for syn in wordnet.synsets("good"): 
    for l in syn.lemmas(): 
        synonyms.append(l.name()) 
        if l.antonyms(): 
            antonyms.append(l.antonyms()[0].name()) 
  
print(set(synonyms)) 
print(set(antonyms)) 

trial
['a sample for ten days free trial', 'a trial of progesterone failed to relieve the pain']
{'salutary', 'dear', 'effective', 'respectable', 'soundly', 'ripe', 'trade_good', 'in_force', 'unspoiled', 'undecomposed', 'secure', 'practiced', 'skillful', 'well', 'full', 'sound', 'honorable', 'honest', 'estimable', 'proficient', 'skilful', 'adept', 'in_effect', 'expert', 'dependable', 'goodness', 'right', 'good', 'serious', 'thoroughly', 'just', 'beneficial', 'commodity', 'safe', 'unspoilt', 'upright', 'near'}
{'evilness', 'ill', 'bad', 'badness', 'evil'}


In [127]:
# Natural Language Toolkit: code_random_text
nltk.download('genesis')

def generate_model(cfdist, word, num=15):
    for i in range(num):
        print(word, end=' ')
        word = cfdist[word].max()

text = nltk.corpus.genesis.words('english-kjv.txt')
bigrams = nltk.bigrams(text)
cfd = nltk.ConditionalFreqDist(bigrams) # [_bigram-condition]

generate_model(cfd, 'the')

[nltk_data] Downloading package genesis to
[nltk_data]     /Users/ompalmer/nltk_data...
[nltk_data]   Package genesis is already up-to-date!


the land of the land of the land of the land of the land of 

In [338]:
# and loads more...list of corpora http://www.nltk.org/nltk_data/

nltk.download('gutenberg')
nltk.download('brown')
nltk.download('reuters')
nltk.download('inaugural')
nltk.download('names')
nltk.download('reviews')
nltk.download('state_union')


from nltk.corpus import gutenberg
from nltk.corpus import brown
from nltk.corpus import reuters
from nltk.corpus import inaugural
from nltk.corpus import names
from nltk.corpus import state_union



# print(gutenberg.fileids())
# print(brown.fileids())
# print(reuters.fileids())
# print(names.fileids())

# for i in range(100):
#     print(brown.words()[i])
# print(brown.words()[0:1000])



[nltk_data] Downloading package gutenberg to
[nltk_data]     /Users/ompalmer/nltk_data...
[nltk_data]   Package gutenberg is already up-to-date!
[nltk_data] Downloading package brown to /Users/ompalmer/nltk_data...
[nltk_data]   Package brown is already up-to-date!
[nltk_data] Downloading package reuters to
[nltk_data]     /Users/ompalmer/nltk_data...
[nltk_data]   Package reuters is already up-to-date!
[nltk_data] Downloading package inaugural to
[nltk_data]     /Users/ompalmer/nltk_data...
[nltk_data]   Package inaugural is already up-to-date!
[nltk_data] Downloading package names to /Users/ompalmer/nltk_data...
[nltk_data]   Package names is already up-to-date!
[nltk_data] Error loading reviews: Package 'reviews' not found in
[nltk_data]     index
[nltk_data] Downloading package state_union to
[nltk_data]     /Users/ompalmer/nltk_data...
[nltk_data]   Package state_union is already up-to-date!


Abagael
Abagail
Abbe
Abbey
Abbi
Abbie
Abby
Abigael
Abigail
Abigale
Abra
Acacia
Ada
Adah
Adaline
Adara
Addie
Addis
Adel
Adela
Adelaide
Adele
Adelice
Adelina
Adelind
Adeline
Adella
Adelle
Adena
Adey
Adi
Adiana
Adina
Adora
Adore
Adoree
Adorne
Adrea
Adria
Adriaens
Adrian
Adriana
Adriane
Adrianna
Adrianne
Adrien
Adriena
Adrienne
Aeriel
Aeriela
Aeriell
Ag
Agace
Agata
Agatha
Agathe
Aggi
Aggie
Aggy
Agna
Agnella
Agnes
Agnese
Agnesse
Agneta
Agnola
Agretha
Aida
Aidan
Aigneis
Aila
Aile
Ailee
Aileen
Ailene
Ailey
Aili
Ailina
Ailyn
Aime
Aimee
Aimil
Aina
Aindrea
Ainslee
Ainsley
Ainslie
Ajay
Alaine
Alameda
Alana
Alanah
Alane
Alanna
Alayne
Alberta
Albertina
Albertine
Albina
Alecia
Aleda
Aleece
Aleecia
Aleen
Alejandra
Alejandrina
Alena
Alene
Alessandra
Aleta
Alethea
Alex
Alexa
Alexandra
Alexandrina
Alexi
Alexia
Alexina
Alexine
Alexis
Alfie
Alfreda
Ali
Alia
Alica
Alice
Alicea
Alicia
Alida
Alidia
Alina
Aline
Alis
Alisa
Alisha
Alison
Alissa
Alisun
Alix
Aliza
Alla
Alleen
Allegra
Allene
Alli
Allianora
Allie
A

Corrina
Corrine
Corrinne
Corry
Cortney
Cory
Cosetta
Cosette
Courtenay
Courtney
Cresa
Cris
Crissie
Crissy
Crista
Cristabel
Cristal
Cristen
Cristi
Cristie
Cristin
Cristina
Cristine
Cristionna
Cristy
Crysta
Crystal
Crystie
Cyb
Cybal
Cybel
Cybelle
Cybil
Cybill
Cyndi
Cyndy
Cynthea
Cynthia
Cynthie
Cynthy
Dacey
Dacia
Dacie
Dacy
Dael
Daffi
Daffie
Daffy
Dafna
Dagmar
Dahlia
Daile
Daisey
Daisi
Daisie
Daisy
Dale
Dalenna
Dalia
Dalila
Dallas
Daloris
Damara
Damaris
Damita
Dana
Danell
Danella
Danelle
Danette
Dani
Dania
Danica
Danice
Daniel
Daniela
Daniele
Daniella
Danielle
Danika
Danila
Danit
Danita
Danna
Danni
Dannie
Danny
Dannye
Danya
Danyelle
Danyette
Daphene
Daphna
Daphne
Dara
Darb
Darbie
Darby
Darcee
Darcey
Darci
Darcie
Darcy
Darda
Dareen
Darell
Darelle
Dari
Daria
Darice
Darla
Darleen
Darlene
Darline
Darryl
Darsey
Darsie
Darya
Daryl
Daryn
Dasha
Dasi
Dasie
Dasya
Datha
Daune
Daveen
Daveta
Davida
Davina
Davine
Davita
Dawn
Dawna
Dayle
Dayna
Dea
Deana
Deane
Deanna
Deanne
Deb
Debbi
Debbie
Debbra
Debby


Jacquie
Jacynth
Jada
Jade
Jaime
Jaimie
Jaine
Jaleh
Jami
Jamie
Jamima
Jammie
Jan
Jana
Janaya
Janaye
Jandy
Jane
Janean
Janeczka
Janeen
Janel
Janela
Janella
Janelle
Janene
Janenna
Janessa
Janet
Janeta
Janetta
Janette
Janeva
Janey
Jania
Janice
Janie
Janifer
Janina
Janine
Janis
Janith
Janka
Janna
Jannel
Jannelle
Janot
Jany
Jaquelin
Jaquelyn
Jaquenetta
Jaquenette
Jaquith
Jasmin
Jasmina
Jasmine
Jayme
Jaymee
Jayne
Jaynell
Jazmin
Jean
Jeana
Jeane
Jeanelle
Jeanette
Jeanie
Jeanine
Jeanna
Jeanne
Jeannette
Jeannie
Jeannine
Jehanna
Jelene
Jemie
Jemima
Jemimah
Jemmie
Jemmy
Jen
Jena
Jenda
Jenelle
Jenette
Jeni
Jenica
Jeniece
Jenifer
Jeniffer
Jenilee
Jenine
Jenn
Jenna
Jennee
Jennette
Jenni
Jennica
Jennie
Jennifer
Jennilee
Jennine
Jenny
Jeraldine
Jeralee
Jere
Jeri
Jermaine
Jerrie
Jerrilee
Jerrilyn
Jerrine
Jerry
Jerrylee
Jess
Jessa
Jessalin
Jessalyn
Jessamine
Jessamyn
Jesse
Jesselyn
Jessi
Jessica
Jessie
Jessika
Jessy
Jewel
Jewell
Jewelle
Jill
Jillana
Jillane
Jillayne
Jilleen
Jillene
Jilli
Jillian
Jillie
J

Melessa
Melicent
Melina
Melinda
Melinde
Melisa
Melisande
Melisandra
Melisenda
Melisent
Melissa
Melisse
Melita
Melitta
Mella
Melli
Mellicent
Mellie
Mellisa
Mellisent
Mellissa
Melloney
Melly
Melodee
Melodie
Melody
Melonie
Melony
Melosa
Melva
Mercedes
Merci
Mercie
Mercy
Meredith
Meredithe
Meridel
Meridith
Meriel
Merilee
Merilyn
Meris
Merissa
Merl
Merla
Merle
Merlina
Merline
Merna
Merola
Merralee
Merridie
Merrie
Merrielle
Merrile
Merrilee
Merrili
Merrill
Merrily
Merry
Mersey
Meryl
Meta
Mia
Micaela
Michaela
Michaelina
Michaeline
Michaella
Michal
Michel
Michele
Michelina
Micheline
Michell
Michelle
Micki
Mickie
Micky
Midge
Mignon
Mignonne
Miguela
Miguelita
Mikako
Mildred
Mildrid
Milena
Milicent
Milissent
Milka
Milli
Millicent
Millie
Millisent
Milly
Milzie
Mimi
Min
Mina
Minda
Mindy
Minerva
Minetta
Minette
Minna
Minni
Minnie
Minny
Minta
Miquela
Mira
Mirabel
Mirabella
Mirabelle
Miran
Miranda
Mireielle
Mireille
Mirella
Mirelle
Miriam
Mirilla
Mirna
Misha
Missie
Missy
Misti
Misty
Mitra
Mitzi
Mmaria

Tessi
Tessie
Tessy
Thalia
Thea
Theada
Theadora
Theda
Thekla
Thelma
Theo
Theodora
Theodosia
Theresa
Theresa-Marie
Therese
Theresina
Theresita
Theressa
Therine
Thia
Thomasa
Thomasin
Thomasina
Thomasine
Tia
Tiana
Tiena
Tierney
Tiertza
Tiff
Tiffani
Tiffanie
Tiffany
Tiffi
Tiffie
Tiffy
Tilda
Tildi
Tildie
Tildy
Tillie
Tilly
Tim
Timi
Timmi
Timmie
Timmy
Timothea
Tina
Tine
Tiphani
Tiphanie
Tiphany
Tish
Tisha
Tobe
Tobey
Tobi
Tobie
Toby
Tobye
Toinette
Toma
Tomasina
Tomasine
Tomi
Tomiko
Tommi
Tommie
Tommy
Toni
Tonia
Tonie
Tony
Tonya
Tootsie
Torey
Tori
Torie
Torrie
Tory
Tova
Tove
Trace
Tracee
Tracey
Traci
Tracie
Tracy
Trenna
Tresa
Trescha
Tressa
Tricia
Trina
Trish
Trisha
Trista
Trix
Trixi
Trixie
Trixy
Truda
Trude
Trudey
Trudi
Trudie
Trudy
Trula
Tuesday
Twila
Twyla
Tybi
Tybie
Tyne
Ula
Ulla
Ulrica
Ulrika
Ulrike
Umeko
Una
Ursa
Ursala
Ursola
Ursula
Ursulina
Ursuline
Uta
Val
Valaree
Valaria
Vale
Valeda
Valencia
Valene
Valenka
Valentia
Valentina
Valentine
Valera
Valeria
Valerie
Valery
Valerye
Valida
Valin

Forest
Forester
Forrest
Forrester
Forster
Foster
Fowler
Fox
Fran
Francesco
Francis
Francisco
Francois
Frank
Frankie
Franklin
Franklyn
Franky
Frans
Franz
Fraser
Frazier
Fred
Freddie
Freddy
Frederic
Frederich
Frederick
Frederico
Frederik
Fredric
Fredrick
Freeman
Freemon
Fremont
French
Friedric
Friedrich
Friedrick
Fritz
Fulton
Fyodor
Gabe
Gabriel
Gabriele
Gabriell
Gabriello
Gail
Gale
Galen
Gallagher
Gamaliel
Garcia
Garcon
Gardener
Gardiner
Gardner
Garey
Garfield
Garfinkel
Garold
Garp
Garret
Garrett
Garrot
Garrott
Garry
Garth
Garv
Garvey
Garvin
Garvy
Garwin
Garwood
Gary
Gaspar
Gasper
Gaston
Gav
Gaven
Gavin
Gavriel
Gay
Gayle
Gearard
Gene
Geo
Geof
Geoff
Geoffrey
Geoffry
Georg
George
Georges
Georgia
Georgie
Georgy
Gerald
Geraldo
Gerard
Gere
Gerhard
Gerhardt
Geri
Germaine
Gerold
Gerome
Gerrard
Gerri
Gerrit
Gerry
Gershom
Gershon
Giacomo
Gian
Giancarlo
Giavani
Gibb
Gideon
Giff
Giffard
Giffer
Giffie
Gifford
Giffy
Gil
Gilbert
Gilberto
Gilburt
Giles
Gill
Gilles
Ginger
Gino
Giordano
Giorgi
Giorgio
G

Randie
Randolf
Randolph
Randy
Ransell
Ransom
Raoul
Raphael
Raul
Ravi
Ravil
Rawley
Ray
Raymond
Raymund
Raymundo
Raynard
Rayner
Raynor
Reagan
Red
Redford
Redmond
Reece
Reed
Rees
Reese
Reg
Regan
Regen
Reggie
Reggis
Reggy
Reginald
Reginauld
Reid
Reilly
Reinhard
Reinhold
Rem
Remington
Remus
Renado
Renaldo
Renard
Renato
Renaud
Renault
Rene
Reube
Reuben
Reuven
Rex
Rey
Reynard
Reynold
Reynolds
Reza
Rhett
Ric
Ricard
Ricardo
Riccardo
Rice
Rich
Richard
Richardo
Richie
Richmond
Richy
Rick
Rickard
Rickey
Ricki
Rickie
Ricky
Rik
Rikki
Riley
Rinaldo
Ripley
Ritch
Ritchie
Roarke
Rob
Robb
Robbert
Robbie
Robert
Roberto
Robin
Robinson
Rochester
Rock
Rockwell
Rocky
Rod
Rodd
Roddie
Roddy
Roderic
Roderich
Roderick
Roderigo
Rodge
Rodger
Rodney
Rodolfo
Rodolph
Rodolphe
Rodrick
Rodrigo
Rodrique
Rog
Roger
Rogers
Roice
Roland
Rolando
Rolf
Rolfe
Rolland
Rollin
Rollins
Rollo
Rolph
Romain
Roman
Romeo
Ron
Ronald
Ronen
Roni
Ronnie
Ronny
Roosevelt
Rory
Roscoe
Ross
Roth
Rourke
Rowland
Roy
Royal
Royce
Rube
Ruben
Rubin
Rub

In [130]:
from nltk.corpus import words
from random import sample
n = 100
rand_words = ' '.join(sample(words.words(), n))
print(rand_words)

kanat bohireen periodical purringly Congolese trabecule tellsome Cristatella arthral recaption apprenticehood overstring Achyranthes tublike Gruiformes bedevil serene interfilar progger interstrial roughhousing gelatinizer rattish minaret overlavish enrut Zenaidura mousetail Hephaestus showyard microbiologically pentaglot decoherence bichromatize chondropharyngeus scotomy polygon funnyman disoxygenation cholanic nocuously sarcilis proceritic sketchist zygotene precondemnation Gregarinoidea pearceite gurgly superterrestrial oblanceolate uncircumcisedness compromising presenced dichroic supersensuous sunbreak amygdalate edulcoration talliage felsite prelachrymal opuscular steersman professionize pygmyish Clisiocampa angiohypertonia kat Russelia spirale woolworking yon mithridatic unfrequentness procreatress cerotype leecher didynamy familiarization auspiciousness molassy unberufen unmendable presanctified cisalpine uvea fulguration lightwort jounce Huxleian octogenary unwrapper ultraemph

In [165]:
from nltk.corpus import wordnet
from nltk.stem import WordNetLemmatizer
lemmatizer = WordNetLemmatizer()
# print(lemmatizer.lemmatize("cats"))

nouns = []
verbs = []
adjectives = []

for synset in list(wordnet.all_synsets('n')):
    # do different things
    # print(synset) # print the synset
    # print(synset.lemma_names()[0]) # print just the word

    word = lemmatizer.lemmatize(synset.lemma_names()[0]).replace("_"," ")
    nouns.append(word)

print('nouns',nouns)

nouns ['entity', 'physical entity', 'abstraction', 'thing', 'object', 'whole', 'congener', 'living thing', 'organism', 'benthos', 'dwarf', 'heterotroph', 'parent', 'life', 'biont', 'cell', 'causal agent', 'person', 'animal', 'plant', 'native', 'natural object', 'substance', 'substance', 'matter', 'food', 'nutrient', 'artifact', 'article', 'psychological feature', 'cognition', 'motivation', 'attribute', 'state', 'feeling', 'location', 'shape', 'time', 'space', 'absolute space', 'phase space', 'event', 'process', 'act', 'group', 'relation', 'possession', 'social relation', 'communication', 'measure', 'phenomenon', 'thing', 'kindness', 'abdominoplasty', 'abort', 'accomplishment', 'agon', 'alienation', 'application', 'beachhead', 'cakewalk', 'feat', 'masterpiece', 'masterstroke', 'credit', 'action', 'res gestae', 'course', 'blind alley', 'collision course', 'interaction', 'interplay', 'contact', 'brush', 'eye contact', 'fetch', 'placement', 'interchange', 'reciprocity', 'cross-fertilizatio

In [167]:
from nltk.corpus import wordnet
from nltk.stem import WordNetLemmatizer
lemmatizer = WordNetLemmatizer()
# print(lemmatizer.lemmatize("cats"))

nouns = []
verbs = []
adjectives = []

for synset in list(wordnet.all_synsets('n')):
    word = lemmatizer.lemmatize(synset.lemma_names()[0]).replace("_"," ")
    nouns.append(word)
for synset in list(wordnet.all_synsets('v')):
    word = lemmatizer.lemmatize(synset.lemma_names()[0]).replace("_"," ")
    verbs.append(word)
for synset in list(wordnet.all_synsets('a')):
    word = lemmatizer.lemmatize(synset.lemma_names()[0]).replace("_"," ")
    adjectives.append(word)


print('nouns',nouns[0:10])
print('verbs',verbs[0:10])
print('adjectives',adjectives[0:10])

nouns ['entity', 'physical entity', 'abstraction', 'thing', 'object', 'whole', 'congener', 'living thing', 'organism', 'benthos']
verbs ['breathe', 'respire', 'respire', 'choke', 'hyperventilate', 'hyperventilate', 'aspirate', 'burp', 'force out', 'hiccup']
adjectives ['able', 'unable', 'abaxial', 'adaxial', 'acroscopic', 'basiscopic', 'abducent', 'adducent', 'nascent', 'emergent']


In [192]:
# let's try to extract VBG nouns (Verb, gerund or present participle)
# (later on we'll use NNP + NNS for noun, proper)

# starting with a basic sentence

sentence = "At eight o'clock on extracting Thursday film morning word line test best beautiful Ram Aaron design"
tokens = nltk.word_tokenize(sentence)
tagged = nltk.pos_tag(tokens)
length = len(tagged) - 1
vbg = [item[0] for item in tagged if item[1]== 'VBG']
nnp = [item[0] for item in tagged if item[1]== 'NNP']
nns = [item[0] for item in tagged if item[1]== 'NNS']

print(vbg,nnp,nns)

['extracting'] ['Thursday', 'Ram', 'Aaron'] []


In [342]:
# now let's create huge lists of nouns

sentence = ''
for synset in list(wordnet.all_synsets('n')):
    word = lemmatizer.lemmatize(synset.lemma_names()[0]).replace("_"," ")
    sentence = sentence + word + ' '
tokens = nltk.word_tokenize(sentence)
tagged = nltk.pos_tag(tokens)
length = len(tagged) - 1

vbg = [item[0] for item in tagged if item[1]== 'VBG']
nnp = [item[0] for item in tagged if item[1]== 'NNP']
nns = [item[0] for item in tagged if item[1]== 'NNS']

In [356]:
adj = []
for synset in list(wordnet.all_synsets('a')):
    word = lemmatizer.lemmatize(synset.lemma_names()[0]).replace("_"," ")
    adj.append(word)
    
print(adj)

['able', 'unable', 'abaxial', 'adaxial', 'acroscopic', 'basiscopic', 'abducent', 'adducent', 'nascent', 'emergent', 'dissilient', 'parturient', 'dying', 'moribund', 'last', 'abridged', 'cut', 'half-length', 'potted', 'unabridged', 'full-length', 'absolute', 'direct', 'implicit', 'infinite', 'living', 'relative', 'relational', 'absorbent', 'absorbefacient', 'assimilating', 'hygroscopic', 'receptive', 'shock-absorbent', 'spongy', 'thirsty', 'nonabsorbent', 'repellent', 'adsorbent', 'chemisorptive', 'nonadsorbent', 'absorbable', 'adsorbable', 'abstemious', 'abstinent', 'ascetic', 'gluttonous', 'crapulous', 'crapulent', 'edacious', 'greedy', 'hoggish', 'overgreedy', 'abstract', 'conceptional', 'conceptual', 'ideal', 'ideological', 'concrete', 'objective', 'real', 'abundant', 'abounding', 'ample', 'copious', 'easy', 'exuberant', 'thick', 'long', 'overabundant', 'plentiful', 'rampant', 'rank', 'superabundant', 'teeming', 'torrential', 'verdant', 'scarce', 'rare', 'tight', 'abused', 'battered

In [262]:
# so, let's convert these grammar lists into tracery items

rules = {
    "master":"[#setcategory#]#category##additional#\n==",
    "setcategory":["[category:#cat#],[subcat:#additional#]"],
    "cat":["#noun.capitalize.s#","#noun.capitalize.s#","#adj.capitalize# #noun.capitalize# #vbg.capitalize#","#adj.capitalize# #vbg.capitalize#","#adj.capitalize# #vbg.capitalize#","#adj.capitalize# #vbg.capitalize.s#","#adj.capitalize# #vbg.capitalize#"],
    "vbg":vbg,
    "noun":["#nnp.capitalize#","#nns.capitalize#","#modifier##nns#"],
    "nnp":nnp,
    "nns":nns,
    "adj":adj,
    "additional":["","",""," (#noun.capitalize#)"," (#noun.capitalize#, #noun.capitalize#)"," (#noun.capitalize#, #adj.capitalize# & #adj.capitalize#)"," (NOT #noun.capitalize#)"],
    "modifier":["","","","","","Paleo","Crypto","Pseudo","Trans","Neuro","Arch","Pre-","Post-","X-","Anarcho",],
}

grammar = tracery.Grammar(rules) # create a grammar object from the rules
grammar.add_modifiers(base_english) # add pre-programmed modifiers

for i in range(100):
    print (grammar.flatten("#master#")) # and flatten, starting with origin rule

Forty-third Teaching
==
Noncombustible Egyptian String (Madison)
==
Legato Japanese Tinning (Fits, Removed & Sentimental)
==
Ready Cupping
==
Lavish Ashes Developing (Drink, Onomastics)
==
Armadas (Archchicken, Logical & Envisioned)
==
Unplowed Calving
==
Accipiters (NOT Foreign)
==
Awkward Reburying (Dynamics, Quixotic & Regular)
==
Hydroelectric Charming (NOT Mandela)
==
Secondary Tying (Plains, Lethargic & Minor)
==
Button-shaped Rings (Sales)
==
Indulgent Middling
==
Transglutens
==
Footlightses (Lake, Witchlike & Microbial)
==
Technophobic Ping (Genus, Customs)
==
Pukka Everlasting (Genus, Stores)
==
Purifying Dressing (Dos)
==
Wet Giving
==
Fundamental Recycling (Bacteria, Paleophonics)
==
Onside Ringhals Retaining
==
Deuteranopic Sleeping
==
Metamorphic Filing (Diacalpa, Archresources)
==
Imperial Sucking (NOT Cryptoaccounts)
==
Parabolic Filming (Psychodynamics, Avens)
==
Foolhardy Bullring
==
Erins (Rattle, Dead & Existential)
==
Anarcholinguisticses
==
Apt Medal Lemming (Cyri

In [367]:
# "#something.capitalize# #category.s.capitalize#",
# "#initials# #category.capitalize#",
# "#initials# #superlative.capitalize# #category.capitalize.s#",
# "#town# #category.capitalizeAll#",
# "#firstname#\'s #category.capitalizeAll#",
# "#firstname#\'s #superlative.capitalize# #category.capitalize#",
# "#firstname#\'s #category.capitalize.s#",
# "#initials.capitalizeAll# #surname# (#category.capitalize#)",
# "#initials.capitalizeAll# #surname.capitalize# #modifier.capitalize#",
# "#initials.capitalizeAll# #surname.capitalize#",
# "#initials.capitalizeAll# #noun.capitalize#",
# "#noun.capitalize#",
# "#adj.capitalize# #noun.capitalize#",


rules = {
    # category
    "master":"[#setcategory#]#category##additional#\n=================\n",
    "setcategory":["[adj:#setadj#],[category:#cat#],[subcat:#additional#],[noun:#setnoun#],[additional:#setadditional#]"],
    "cat":["#noun.capitalize.s#","#noun.capitalize.s#","#adj.capitalize# #noun.capitalize# #vbg.capitalize#","#adj.capitalize# #vbg.capitalize#","#adj.capitalize# #vbg.capitalize#","#adj.capitalize# #vbg.capitalize.s#","#adj.capitalize# #vbg.capitalize#"],
    "vbg":vbg,
    "setnoun":["#nnp.capitalize#","#nns.capitalize#","#modifier##nns#"],
    "nnp":nnp,
    "nns":nns,
    "setadj":adj,
    "setadditional":["","",""," (#noun.capitalize#)"," (#noun.capitalize#, #noun.capitalize#)"," (#noun.capitalize#, #adj.capitalize# & #adj.capitalize#)"," (NOT #noun.capitalize#)"],
    "modifier":["","","","","","Paleo","Crypto","Pseudo","Trans","Neuro","Arch","Pre-","Post-","X-","Anarcho",],

    # companies
    "listing":["[#companyinfo#]\*\*#name.capitalize#\*\*\ \ \n\_#motto#\_\ \ \n#address#\ \ \n☎ #phone#\n\n"],

    # set company info
    "companyinfo":["[town:#settown#],[name:#setname#],[address:#setaddress#],[phone:#setphone#],[motto:#setmotto#]"],

    # town
    "settown":"#prefix.capitalize##suffix#",
    "prefix": townprefixes,
    "suffix": townsuffixes,

    # company name
      "setname":[
        "#something.capitalize# #category.s.capitalize#",
        "#initials# #category.capitalize#",
        "#initials# #superlative.capitalize# #category.capitalize.s#",
        "#initials.capitalizeAll# #noun.capitalize# #and.capitalize#",
        "#noun.capitalize# #and.capitalize#",
        "#initials.capitalizeAll# #noun.capitalize#",
        "#initials.capitalizeAll# #surname# (#category.capitalize#)",
        "#initials.capitalizeAll# #noun.capitalize# #and.capitalize#",
        "#category.capitalize# (#initials.capitalizeAll# #surname.capitalize# #and#)",
        "#firstname.capitalize#\'s #category.capitalize#",
        "#firstname.capitalize#\'s #noun.capitalize#",
        "#town.capitalize# #adj.capitalize#",
        "#town.capitalize# #noun.capitalize#",
        "#town.capitalize# #category.capitalize#",
        "#town.capitalize# #adj.capitalize# #and#",
        "#town.capitalize# #noun.capitalize# #and",
        "#town.capitalize# #category.capitalize# #and#",
        "#initials.capitalizeAll##initials.capitalizeAll##initials.capitalizeAll# #and#",
        "#initials.capitalizeAll# #and# (#town.capitalize#)",
        "#noun.capitalize# #and.capitalize#",
        "#firstname#\'s #superlative.capitalize# #category.capitalize#",
        "#setadj.capitalize# #noun.capitalize# #initials.capitalizeAll#"
      ],
    "initials":["#l.capitalize#.","#l.capitalize#.#l.capitalize#.#l.capitalize#.#l.capitalize#.#l.capitalize#.#l.capitalize#.","#l.capitalize#.#l.capitalize#.","#l.capitalize##l.capitalize#","#firstname.capitalize# #l.capitalize#."],
    "l":["a","b","c","d","e","f","g","h","i","j","k","l","m","n","o","p","q","r","s","t","u","v","w","x","y","z"],
    "firstname":firstnames,
    "surname":surnames,
    "and":["& Sons","& Co","and Company","Incorporated","& #nnp.capitalize#","Holdings"],


    # address
    "setaddress": "#streetname.capitalize#, #town.capitalize#",
    "number": ["#d0#","#d0##d#","#d0##d##d#","#d0##d##d#","#d0##d##d#","#d0##d##d#","#d0##d##d##d#","#d0##d##d##d#","#d0##d##d##d#","#d0##d##d##d#","#d0##d##d##d#","#d0##d##d##d#","#d0##d##d##d#","#d0##d##d##d#","#d0##d##d##d#"],
    "streetname":["#number# #street# #streettype#","#number# #street# #streettype#","#street# & #street#"],
    "streettype":["Avenue","Street","Road","Lane","Parkway","St","Ave"],
    "street": street,
    "town": "#prefix.capitalize##suffix#",
    "prefix": townprefixes,
    "suffix": townsuffixes,
    "zipcode": "#d##d##d##d##d#",
    "d":["0","1","2","3","4","5","6","7","8","9"],
    "d0":["1","2","3","4","5","6","7","8","9"],
    "d1":["0","1"],
    "d19":["18","19","19"],
    "d20":["20"],

    # phone number
    "setphone":["#d0##d##d#-#d##d##d##d#"],


    # motto
    "setmotto": ["#motto#","#tellem#","#weputthexiny#","#weputthexiny#","The #superlative# #thing# #located# #town#","#owned.capitalize#","#stuff#","#directions#","#youlike##punctuation#","#youlike# \n#directions#","#localpromo#"],
    "owned":["#division.a# of #something.capitalize# #inc#","#division.a# of #something.capitalize# #inc.capitalize#","Part of the #something.capitalize# #inc#"],
    "owned2":["#division.a# of #acronym.capitalize# #inc#","#division.a# of #acronym.capitalize# #inc.uppercase#","Part of the #acronym.capitalize# #inc#"],
    "acronym": ["#letter.uppercase#.#letter.uppercase#.","#letter.uppercase#.#letter.uppercase#.#letter.uppercase#.","#letter.uppercase##letter.uppercase##letter.uppercase#","#letter.uppercase##letter.uppercase##letter.uppercase##letter.uppercase#","#letter.uppercase##letter.uppercase##letter.uppercase##letter.uppercase##letter.uppercase#","#letter.uppercase#-#letter.uppercase#-#letter.uppercase#-#letter.uppercase#"],
    "inc": ["Family","Network","Network of Companies","LLC","PLC","L.L.C."],
    "something": ["#nnp#","#nns#"],
    "division":["Proud Member","Founding Member"],
    "superlative": ["biggest","best","oldest","rarest","most sought-after","nicest","prettiest"],
    "thing": ["prices","selection","collection","range","budget option","#size# selection"],
    "size": ["mid-range","large-scale","huge","budget","high budget","upscale"],
    "located": ["in","near","#dir# of"],
    "dir": ["north","south","east","west","just outside"],
    "stuff": ["#something.capitalize#, #something.capitalize#, & #something.capitalize#!","#something.capitalize# • #something.capitalize# • #something.capitalize#","#wevegot# #something.capitalize#!"],
    "wevegot": ["We've got","You'll love our","Why not try","Take a look at our","Relax with","Prod our"],
    "directions":["#action# #dir# at #town#","#action# #dir# at #place#, #action# for #distance# #measurement#","#place.capitalize#: #action# #dir# at #town#, #action# #dir# at #town#, #action# #dir# at #town#"],
    "place":["#town#","Junction #d0##d#","Interstate #d0##d#","the #something.capitalize#"],
    "action":["Turn","Continue Straight","Continue","Drive"],
    "distance": ["#d0#","#d0##d#"],
    "measurement":["miles","feet"],
    "youlike":[
        "#something.capitalize# #timespan#!",
        "You like #stuff.capitalize#? We've got it!",
        "Have you ever wanted #something.capitalize#?",
        "Have you ever wanted #something.capitalize#? We have #something.capitalize#!",
        "Dreaming of #something.capitalize#?!",
        "Why not try #something.capitalize# #timespan#?",
        "You want #category.capitalize#? We've got #category.capitalize#!",
        "#category.capitalize#: Just the way you like it",
        "You've never seen #category.capitalize# this #size#",
        "Our secret is in our #nnp.capitalize#",
        "Family owned #nns.capitalize#",
    ],
    "timespan":["now","tomorrow","today","right now","immediately","the next chance you get"],
    "weputthe":["We put the #something# in #something.s#"],
    "tell":["Tell them","Tell 'em","Just say"],
    "amazingjob":["#qualifier# #job#"],
    "qualifier":["top","local celebrity","well-known","your favourite","imaginary friend","family favourite","the one and only","phenomenal","the best","excellent","mediocre","mid-range","smooth moving"],
    "job":["chef","TV host","Psychic","carpenter","dentist","orthodontist","paleontologist","captain","musician"],
    "tellem":["#tell# #firstname# sent you!","Recommended by #amazingjob# #firstname.capitalize# #surname.capitalize#"],
    "tell":["Tell them","Tell 'em","Just say"],
    "est":["Established #year#","Since #year#","Serving #town# since #year#","Helping you with #category# since #year#","In #town.capitalize# since #year#"],
    "year":["#d19##d##d#","#d19##d##d#","#d20##d1##d#"],
    "punctuation":["!",".","!!","!","!!!","?!"],


    "weputthexiny":["#weputthe#!","#weputthe#!!!","#weputthe#"],
    "weputthe":weputthe,
    "localpromo":["Hear our advert on #localstation#","You might have heard about us on #localstation#","Proud sponsors of #localstation#"],
    "localstation":["#something.capitalize# #d0##d#.#d0# FM","#qualifier# local station #something.capitalize# #d0##d#.#d0# FM","1#d##d#.#d0# FM","the Internet","the radio"]
}




grammar = tracery.Grammar(rules) # create a grammar object from the rules
grammar.add_modifiers(base_english) # add pre-programmed modifiers


import random

for i in range(100):
    print (grammar.flatten("#master#")) # and flatten, starting with origin rule
    for j in range(random.randrange(1,15)):
        print("\n",grammar.flatten("#listing#"))

Heavenward Flyings


 **Bravodam Transworkmen**  
_Hear our advert on 173.4 FM_  
5361 Pleasant Avenue, Bravodam  
☎ 308-5014



 **Physics Heavenward Flyingses**  
_Parks, Lexington, & Ballistics!_  
Broadway & Oxford, Whiskeychester  
☎ 142-5650



 **Trade Heavenward Flyingses**  
_The prettiest selection east of Hotelfield_  
Johnson & Pecan, Hotelfield  
☎ 993-1615



 **Victorport Heavenward Holdings**  
_We put the "ammonite" in "mammonite"_  
898 Bow Ave, Victorport  
☎ 841-2568


Connected Renderings


 **Kilostone Connected Renderings Incorporated**  
_You've never seen Connected Renderings this upscale._  
4553 Johnson Ave, Kilostone  
☎ 929-9914



 **Charlieston Hydrodamalis**  
_Drive south at Junction 54, Turn for 42 feet_  
112th & Regent, Charlieston  
☎ 431-2701



 **P. Hydrodamalis Incorporated**  
_Part of the Bridge Network_  
6959 Marylebone Road, Yankeechester  
☎ 884-0427


Trial-and-error Darling


 **L.R.U.F.A.K. Reticulum And Company**  
_Proud sponsors of m


 **Mural Measures F.**  
_Newt • Acrobates • Thoracic_  
King’s Cross & West, Kilodam  
☎ 266-9490



 **Uniformford Unkind Lining**  
_We put the "aster" in "kollaster"!!!_  
4th & Church, Uniformford  
☎ 805-2645



 **Wolfy Q. Measures & Co**  
_We put the "ess" in "associativeness"!!!_  
4919 Lee Street, Quebecview  
☎ 362-1243


Slender Ring


 **Kenton S. Slender Ring**  
_We put the "less" in "scapeless"!!!_  
Fenchurch & Hillside, Deltaburn  
☎ 357-2198



 **Cross-cultural Pseudowords Alisha V.**  
_Slender Ring: Just the way you like it 
Continue just outside at Juliettdam_  
7th & Johnson, Juliettdam  
☎ 621-9489



 **Slender Ring (C.P. Villegas & United)**  
_Part of the Linguistics PLC_  
Aloha & Maple, Echoson  
☎ 375-3189



 **Pseudowords Holdings**  
_Why not try Psycholinguistics now?._  
Lincoln & Bow, Deltaford  
☎ 708-6640


Axenic Raising


 **Q.O.L.H.E.A. National**  
_We've got Yes!_  
5176 Wood Ave, Zuluson  
☎ 517-9098



 **D'Alene Axenic Raisings**  
_You 

 **V.S.V.Z.A.L. Spirochaetaceae & Sons**  
_Continue Straight east at Junction 24, Turn for 3 feet_  
Bond & 9th, Papaster  
☎ 143-1000


Bastioned Greenwing


 **Heterotrophic Forces G.W.**  
_Part of the Hornfels L.L.C._  
1270 Regent St, Kilodam  
☎ 973-3117



 **O. Forces Holdings**  
_A Proud Member of Veins PLC_  
3680 Quail Lane, Golfston  
☎ 881-7092



 **Jeraldine's Bastioned Greenwing**  
_Continue just outside at Kiloside_  
Kansas & Lake, Kiloside  
☎ 930-6319



 **L. Forces Incorporated**  
_Knossos, Gnocchi, & Wigner!_  
1st & Quail, Quebecbridge  
☎ 818-8661



 **Virgilio U.P.X.Arabela D. & Co**  
_We put the "pize" in "misanthropize"_  
Elm & Sunset, Oscarburn  
☎ 184-6545



 **Bastioned Greenwing (Vm Haynes & Sons)**  
_We put the "hi" in "shirakashi"!_  
Evergreen & Ridge, Oscardam  
☎ 773-2557


Forceses (Nicaea, Sikh & Sikh)


 **S.P.Z.G.W.Q. and Company (Foxtrotland)**  
_The rarest collection near Foxtrotland_  
Lehua & Pall, Foxtrotland  
☎ 206-9744



 **Ni

 **Ione's Pachycephalosauruses**  
_Dreaming of Men?!!_  
7856 Palo Verde Avenue, Bravotown  
☎ 531-8012



 **Karrah T. Numbers And Company**  
_We put the "is" in "onychorrhexis"!!!_  
4310 7th Parkway, Romeoster  
☎ 297-4789



 **Numbers & Sons**  
_Part of the Wren Family_  
2012 Bond Lane, Victorson  
☎ 543-7494


Average Living (NOT Post-tears)


 **Deerdre M. Average Living**  
_We put the "ae" in "arborvitae"_  
200 8th St, Oscarview  
☎ 712-0957



 **Hp Post-tears**  
_Dreaming of Port?! 
Drive north at Kiloster_  
593 North Avenue, Kiloster  
☎ 976-5526



 **Limadam Post-tears**  
_Drive north at Limadam, Drive for 72 feet_  
1523 Elm Ave, Limadam  
☎ 121-1404



 **Post-tears Incorporated**  
_Why not try Texas today? 
Echoburn: Drive just outside at Echoburn, Turn north at Echoburn, Drive north at Echoburn_  
127 Fleet Parkway, Echoburn  
☎ 833-0769


Pasty Pruning


 **Noami G. Transglanders & Apache**  
_We put the "nt" in "wariment"!_  
176 Aloha Avenue, Charlieton  



 **S.V. Nicest Impossible Supportings**  
_We put the "or" in "proprioceptor"!_  
8378 Northumberland St, Romeostone  
☎ 663-8195



 **Bessie's Nicest Impossible Supporting**  
_Hear our advert on the radio_  
5667 Pentonville Road, Bravoland  
☎ 799-8868


Transcryonicses


 **Marillin's Archsalts**  
_We put the "pilus" in "mespilus"!!!_  
823 Cherry Lane, Hotelville  
☎ 170-5334



 **Lila's Rarest Transcryonicses**  
_Recommended by your favourite dentist Emmalynn Felix_  
4253 Marlborough Avenue, Yankeeport  
☎ 810-2414



 **Margurite's Nicest Transcryonicses**  
_We put the "led" in "unintitled"!_  
Pentonville & Pinon, Victorster  
☎ 344-7711



 **CD Transcryonicses**  
_Family owned Futures 
Junction 87: Continue south at Xraybridge, Continue east at Xraybridge, Continue Straight east at Xraybridge_  
3112 5th Parkway, Xraybridge  
☎ 402-6568



 **Siward's Transcryonicses**  
_A Founding Member of Hardy L.L.C._  
733 Pinon Road, Uniformville  
☎ 577-6011



 **H. Burns (Tr


 **Phylis O. Nidifugous Disarming**  
_The most sought-after budget option in Foxtrotview_  
Main & Meadow, Foxtrotview  
☎ 471-6921



 **F.T. Tremellales & Sons**  
_We put the "tical" in "antipoetical"_  
4023 Sunset Street, Alfachester  
☎ 383-0184



 **Novemberson Nidifugous**  
_Jamison, Fitzgerald, & Labiatae!_  
2827 Magnolia Avenue, Novemberson  
☎ 945-9126



 **Hotelchester Nidifugous Disarming**  
_We put the "ers" in "bribers"!!!_  
398 Pleasant Lane, Hotelchester  
☎ 842-5097



 **B.Z.H.F.G.L. Tremellales & Co**  
_The nicest budget option in Echoburn_  
219 Hampton Ave, Echoburn  
☎ 732-6287



 **Alvina G. Prettiest Nidifugous Disarmings**  
_Continue west at Deltaford_  
9299 Trafalgar Road, Deltaford  
☎ 194-3981



 **Indiachester Tremellales**  
_You might have heard about us on the one and only local station Lake 12.3 FM_  
Vine & 3rd, Indiachester  
☎ 569-5524



 **Uniformport Nidifugous & Co**  
_A Founding Member of Internal LLC_  
Regent & Shore, Uniformpor

 **I.Z. Fauces And Company**  
_Have you ever wanted Scopes? We have Island!!!_  
3392 Park St, Kiloston  
☎ 812-4258



 **Quebecdam Cornwalls**  
_We put the "theists" in "ditheists"!!!_  
4449 Mountain View Lane, Quebecdam  
☎ 613-7033



 **Zuluburn Cornwalls & Sons**  
_Proud sponsors of the radio_  
4 Redwood Lane, Zuluburn  
☎ 618-0189



 **U.F.O.X.V.R.PkLeonelle P. Holdings**  
_We put the "roof" in "wartproof"!!!_  
Redwood & Juniper, Yankeeford  
☎ 242-7017



 **Tangoston Fauces**  
_Continue Straight north at Interstate 67, Turn for 58 feet_  
5124 Narragansett St, Tangoston  
☎ 155-9740


Fauceses (Data, Floating & Floating)


 **Gymnosperm Fauceseses**  
_Pussytoes • Munitions • Kurd_  
5890 Jackson St, Quebecchester  
☎ 387-1990


Aft Homing (Neurosales, Neurosales)


 **Echoford Aft**  
_You like We've got Sessions!? We've got it!._  
372 Williams Street, Echoford  
☎ 866-6817



 **I.C. Neurosales**  
_Recommended by imaginary friend chef Carson Mckenzie_  
Malulani &

# now onto compiling this nonsense.
# we need to create a new markdown file for each listing
# each md has the following headers

```text
---
name: company name
address: address
phone: phone no.
category: category
big_small: big or small (most should be small)
layout: if big, one two three four or five
motto: motto here
img: image number, between 0000-9999.jpg
---
```

In [ ]:
for i in range(10000):
    grammar.flatten("#master#")
    print(grammar.flatten("#category#"))
    with open('output/pages/'+grammar.flatten("#category#")+'.md','w') as f:
        f.write('---\nlayout:page\ntitle:'+grammar.flatten("#category#")+'\n---\n# '+grammar.flatten("#category#")+'\n\n')
        for j in range(random.randrange(1,30)):
            f.write(grammar.flatten("#listing#")+'\n\n')
            

First-come-first-serve Heckling
Cold Belayings
Noncombustible Coating
Paraboloidal Wedding
Autochthonal Ring
Paperses
Anarchopoilus
Needled Cattle Ringing
Uncensored Sending
Brown-speckled Graduatings
Aggravating Racing
Choric Fingering
Off-line Settings
Hot Jib Receding
Chromodynamicses
Incapable Pricklings
Bitter Cycling
Paninis
Paleopainses
Broadband Ringing
Six-sided Serving
Transgenuses
Categorized Dancings
Wisconsins
Incoming Updating
Partitive Pitching
Xenons
Quintillionth Coloring
Viceregal Spacing
Uncheckable Brainstormings
Frittatas
Nierembergias
Knowable Flyings
Jacksons
Forcepses
Calisthenicses
Ultraviolet Quaking
Disenfranchised Scouting
Archgoodses
Defective Motorcycling
Bernhardts
Mecopterous Transtabes Mourning
Uncombed Groundling
Right-handed Shining
Fortuitous Airing
Clarion Latchstring
Plain Writing
Chocolate-colored Jacking
Senecan Whispering
Broadloom Visiting
Light-handed Stockholding
Perfected Running
Unheated Linemen Interacting
Plierses
Long-spurred Ceras Bounc

Fractional Whispering
Undesirable Rachel Operating
Anarchoreses
Kernels
Iridaceaes
Stretch Groundbreaking
Hot Eating
Forty-fifth Flying
Incursive Spanking
Extendible Keeping
Syllabic Starting
Epidemic Optics Climbing
Intrinsic Patchings
Steerable Riding
Quebecois Sleeping
Attempted Flying
Carunculate Exporting
Ignoble Revolving
Guarneriuses
Dayses
Choragic Stirring
Nidifugous Moving
Trumbulls
Goodses
Indefinite Running
Divisible Feeling
Ancients
Securitieses
Bourgeois Shooting
Adapids
Antiadrenergic Butterfingers Climbing
Standing Rallyings
Bungaloid Rabi Sewing
Achoeroduses
Danishes
Pre-goodses
Effervescent King
Infallible Alkaptonuria Sailing
Pseudosixtiethes
Prepared Abrading
Physas
Antiseptic Post-resources Fishing
Communicable Starting
Physicses
Perceived Marching
Portable Descending
Grey-green Sampling
Primary Damages Loading
Unlawful Riding
Pending Plasterings
Cytoplasmic Haloragidaceae Pleading
Precious Razing
Scentless Programmings
Discalced Printing
Nuclear Quadrupling
Accomm

Heavy Rowing
Incorrigible Lunching
Anarchogymnasticses
Arabics
Gassy Evening
Moderate X-communications Depicting
Tannic Neutering
Dicynodontias
Limitationses
Extended Pigsticking
Delicate Roping
Packaged Dairying
Uninhibited Neurowords Telecommuting
Creditable Frying
Bioluminescent Restings
Refractory Holding
Introjected Ding
Aphyllous Taricha Pinning
Astonishing Earring
Well-branched Ring
Nonrepetitive Waxing
Revitalized Livings
Lipped Weapons Badgering
Tongses
Beatses
Unassailable Dancings
Post-dayses
Metamorphic Everlasting
Saltish Pointings
Anarchoclotheses
Infantile Adding
Icosahedral Archconditions Supping
Stable Handling
Assimilating Grasping
Achondritic Athletics Nursing
Coy Marking
Heterogeneous Burning
Crass Riding
Australians
Veinses
Martens
Major Punchings
Ctenoid Coverings
Intelligences
Graceless Neurotrousers Moneymaking
Extenuating King
Patchy Mixing
Plural Drawings
Regulation Basking
Lesser Racing
Bregmatic Fencing
Steadying Sporting
Cladisticses
Erotic Bleachings
Capsu

Pinioned Kichai Fermenting
Collinsias
Cardiospermums
Goldilockses
Midgards
Rose-colored Crossheading
News
Administrative Mumbling
Light Processing
Mechanicses
Part-time Proportions Reading
Roman Loading
Neurobellses
Azonal Ending
Focal Reading
Overambitious Federalist Reducing
Microeconomicses
Paperses
Plain Flowering
Volumed Drawing
Multipartite Acquiring
Arbitrable Rewordings
Opticses
Oceans
Squarish Packings
Operationses
Epiphyseal Archletters Recording
Ultraconservative Stabling
Microeconomic Scattering
Zapotec Multiprocessing
Savingses
Constructive Skating
Blustery Reading
Acid-tasting Processing
Diastolic Herpes Destroying
Saltses
Genevas
Cautionary Moliere Packing
Thripses
Nascent Central Bearing
Homespun Genus Underwing
Beggar-tickses
Forcepses
Docile Suffering
Septal Encoding
Conopodiums
Obtuse Tineola Meaning
Light Molding
Contrasting Diving
Saleses
Saudi-Arabian Ribbon Skimming
Newborn Rings
Solid-state Reckoning
Close-minded Pudding
Pleased Jacking
Goodses
Visceral People P

Portable Quarrying
Unostentatious Michaelmas Shoestring
Unitary Scabies Everlasting
Ample Peeing
Asynergic Voting
Fail-safe Hairdressing
Excited Tailoring
Acid-forming Papermakings
Paleotrouserses
Bloody-minded Yerba Flying
Dysgenicses
A few Operatings
Clairvoyant Grouping
Anterior Pseudorobotics String
Communicationses
In Flying
Logistic Weeping
Straightforward Thinking
Intaglios
Goodses
Upfront Dining
Wooded Spirits Rolling
Unaccountable Crossings
Tectonic Trousers Bearing
Web-footed Repeating
Cringing Ascending
Puncturable Bits Burning
Psychic Bleeding
Eminent Piping
Circulative Mainspring
Unwitting Trailings
Pumpkins
Involute Typing
Five-membered Racing
Unpresidential Shearing
Cryptobrusselses
Comburent Molding
Disregarded Giving
Gross Seafarings
Brinells
Ungulate Questioning
Mesophytic Voting
Prunes
Beaches
Cardses
Behavioristic Electrodynamics Equalizing
Parotid Doubting
Curly-headses
Weightses
Upfront Ranching
Fulfilled Tiddlywinks Sewing
Knuckses
Rooseveltian Eating
Natural Nur

[nltk_data] Downloading package gutenberg to
[nltk_data]     /Users/ompalmer/nltk_data...
[nltk_data]   Package gutenberg is already up-to-date!
[nltk_data] Downloading package brown to /Users/ompalmer/nltk_data...
[nltk_data]   Package brown is already up-to-date!
[nltk_data] Downloading package reuters to
[nltk_data]     /Users/ompalmer/nltk_data...
[nltk_data]   Package reuters is already up-to-date!
[nltk_data] Downloading package inaugural to
[nltk_data]     /Users/ompalmer/nltk_data...
[nltk_data]   Package inaugural is already up-to-date!
[nltk_data] Downloading package names to /Users/ompalmer/nltk_data...
[nltk_data]   Package names is already up-to-date!
[nltk_data] Error loading reviews: Package 'reviews' not found in
[nltk_data]     index
[nltk_data] Downloading package state_union to
[nltk_data]     /Users/ompalmer/nltk_data...
[nltk_data]   Package state_union is already up-to-date!


The
Fulton
County
Grand
Jury
said
Friday
an
investigation
of
Atlanta's
recent
primary
election
produced
``
no
evidence
''
that
any
irregularities
took
place
.
The
jury
further
said
in
term-end
presentments
that
the
City
Executive
Committee
,
which
had
over-all
charge
of
the
election
,
``
deserves
the
praise
and
thanks
of
the
City
of
Atlanta
''
for
the
manner
in
which
the
election
was
conducted
.
The
September-October
term
jury
had
been
charged
by
Fulton
Superior
Court
Judge
Durwood
Pye
to
investigate
reports
of
possible
``
irregularities
''
in
the
hard-fought
primary
which
was
won
by
Mayor-nominate
Ivan
